In [ ]:
## Load maestro prepped structure into openmm to split chains

In [1]:
import simtk.openmm.app as app

In [2]:
pdb = app.PDBFile("../input/mmc2_no_alt_capped.pdb")

In [3]:
modeller = app.Modeller(pdb.topology, pdb.positions)

In [4]:
chains = list(modeller.topology.chains()) # Chain 0 is A, Chain 1 is F, Chain 2 is water for A, Chain 3 is water for F


In [5]:
modeller.delete([chains[0], chains[2]])

In [6]:
with open("../input/mmc2_barstar.pdb", 'w') as outfile:
    app.PDBFile.writeFile(modeller.topology, modeller.positions, file=outfile, keepIds=True)

In [7]:
pdb = app.PDBFile("../input/mmc2_no_alt_capped.pdb")

In [8]:
modeller = app.Modeller(pdb.topology, pdb.positions)

In [9]:
chains = list(modeller.topology.chains()) # Chain 0 is A, Chain 1 is F, Chain 2 is water for A, Chain 3 is water for F


In [10]:
modeller.delete([chains[1], chains[3]])

In [11]:
with open("../input/mmc2_barnase.pdb", 'w') as outfile:
    app.PDBFile.writeFile(modeller.topology, modeller.positions, file=outfile, keepIds=True)

## Generate htf for T42A

In [1]:
from perses.utils.openeye import *
from perses.annihilation.relative import HybridTopologyFactory
from perses.rjmc.topology_proposal import PointMutationEngine
from perses.rjmc.geometry import FFAllAngleGeometryEngine

import simtk.openmm as openmm
import simtk.openmm.app as app
import simtk.unit as unit
import numpy as np
from openmoltools import forcefield_generators
import copy
import mdtraj as md
from openmmtools.constants import kB
from perses.tests.utils import validate_endstate_energies
from openforcefield.topology import Molecule
from openmmforcefields.generators import SystemGenerator

INFO:numexpr.utils:Note: detected 72 virtual cores but NumExpr set to maximum of 64, check "NUMEXPR_MAX_THREADS" environment variable.
INFO:numexpr.utils:Note: NumExpr detected 72 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
INFO:numexpr.utils:NumExpr defaulting to 8 threads.
RDKit WARNING: [20:38:25] Enabling RDKit 2019.09.3 jupyter extensions


In [2]:
ENERGY_THRESHOLD = 1e-2
temperature = 300 * unit.kelvin
kT = kB * temperature
beta = 1.0/kT



In [55]:
from perses.app.relative_point_mutation_setup import PointMutationExecutor
class PointMutationExecutor2(PointMutationExecutor):
    def __init__(self,
                 protein_filename,
                 mutation_chain_id,
                 mutation_residue_id,
                 proposed_residue,
                 phase='complex',
                 conduct_endstate_validation=True,
                 ligand_filename=None,
                 ligand_index=0,
                 forcefield_files=['amber14/protein.ff14SB.xml', 'amber14/tip3p.xml'],
                 barostat=openmm.MonteCarloBarostat(1.0 * unit.atmosphere, temperature, 50),
                 forcefield_kwargs={'removeCMMotion': False, 'ewaldErrorTolerance': 1e-4, 'constraints' : app.HBonds, 'hydrogenMass' : 4 * unit.amus},
                 periodic_forcefield_kwargs={'nonbondedMethod': app.PME},
                 nonperiodic_forcefield_kwargs=None,
                 small_molecule_forcefields='gaff-2.11',
                 **kwargs):
            super().__init__(
                 protein_filename,
                 mutation_chain_id,
                 mutation_residue_id,
                 proposed_residue,
                 phase='complex',
                 conduct_endstate_validation=True,
                 ligand_filename=ligand_filename,
                 ligand_index=0,
                 forcefield_files=['amber14/protein.ff14SB.xml', 'amber14/tip3p.xml'],
                 barostat=openmm.MonteCarloBarostat(1.0 * unit.atmosphere, temperature, 50),
                 forcefield_kwargs={'removeCMMotion': False, 'ewaldErrorTolerance': 1e-4, 'constraints' : app.HBonds, 'hydrogenMass' : 4 * unit.amus},
                 periodic_forcefield_kwargs={'nonbondedMethod': app.PME},
                 nonperiodic_forcefield_kwargs=None,
                 small_molecule_forcefields='gaff-2.11')
            print(ligand_filename)
    def _solvate(self,
                    topology,
                    positions,
                    model,
                    phase):
        """
        Generate a solvated topology, positions, and system for a given input topology and positions.
        For generating the system, the forcefield files provided in the constructor will be used.

        Parameters
        ----------
        topology : app.Topology
            Topology of the system to solvate
        positions : [n, 3] ndarray of Quantity nm
            the positions of the unsolvated system
        forcefield : SystemGenerator.forcefield
            forcefield file of solvent to add
        model : str, default 'tip3p'
            solvent model to use for solvation

        Returns
        -------
        solvated_topology : app.Topology
            Topology of the system with added waters
        solvated_positions : [n + 3(n_waters), 3] ndarray of Quantity nm
            Solvated positions
        solvated_system : openmm.System
            The parameterized system, containing a barostat if one was specified.
        """
        print("using override solvate function")
        modeller = app.Modeller(topology, positions)


        # Now we have to add missing atoms
        if phase != 'vacuum':
            modeller.addSolvent(self.system_generator.forcefield, model=model, padding=1.0 * unit.nanometers, ionicStrength=0.05*unit.molar)
        else:
            pass

        solvated_topology = modeller.getTopology()
        solvated_positions = modeller.getPositions()

        # Canonicalize the solvated positions: turn tuples into np.array
        solvated_positions = unit.quantity.Quantity(value=np.array([list(atom_pos) for atom_pos in solvated_positions.value_in_unit_system(unit.md_unit_system)]), unit=unit.nanometers)
        solvated_system = self.system_generator.create_system(solvated_topology)

        return solvated_topology, solvated_positions, solvated_system


In [60]:
import pickle 
pickle.dump(solvent_delivery.get_apo_htf(), open("T42A_apo.pickle", "wb" ))
pickle.dump(solvent_delivery.get_complex_htf(), open("T42A_complex.pickle", "wb" ))


In [56]:
# Solvent

solvent_delivery = PointMutationExecutor2("../input/mmc2_barstar.pdb", 
                        '1', # First chain is the barstar one
                        '42', 
                        'ALA',
                        ligand_filename="../input/mmc2_barnase.pdb",
                       )




DEBUG:perses.forcefields.system_generators:Trying GAFFTemplateGenerator to load gaff-2.11


using override solvate function
using override solvate function


INFO:proposal_generator:	Conducting polymer point mutation proposal...
INFO:proposal_generator:[2, 2, 2]
INFO:proposal_generator:Maximum atom matched after hydrogen exceptions: 2
INFO:geometry:propose: performing forward proposal
INFO:geometry:propose: unique new atoms detected; proceeding to _logp_propose...
INFO:geometry:Conducting forward proposal...
INFO:geometry:Computing proposal order with NetworkX...
INFO:geometry:number of atoms to be placed: 2
INFO:geometry:Atom index proposal order is [677, 678]
INFO:geometry:omitted_bonds: []
INFO:geometry:direction of proposal is forward; creating atoms_with_positions and new positions from old system/topology...
INFO:geometry:creating growth system...
INFO:geometry:	creating bond force...
INFO:geometry:	there are 733 bonds in reference force.
INFO:geometry:	creating angle force...
INFO:geometry:	there are 2628 angles in reference force.
INFO:geometry:	creating torsion force...
INFO:geometry:	creating extra torsions force...
INFO:geometry:

conducting subsequent work with the following platform: CUDA


INFO:geometry:setting atoms_with_positions context new positions


...

conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA


INFO:geometry:total reduced energy added from growth system: -64.43004096190329
INFO:geometry:final reduced energy 4736.681371796294
INFO:geometry:sum of energies: 4736.681372670266
INFO:geometry:magnitude of difference in the energies: 8.739719845607397e-07
INFO:geometry:Final logp_proposal: 33.13391558943375


added energy components: [('CustomBondForce', 0.09370408553241331), ('CustomAngleForce', 1.3102816193587339), ('CustomTorsionForce', 9.480381593867468), ('CustomBondForce', -75.31440826066189)]


INFO:relative:Beginning nonbonded method, total particle, barostat, and exceptions retrieval...
INFO:relative:Old system forces: dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce', 'MonteCarloBarostat'])
INFO:relative:New system forces: dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce', 'MonteCarloBarostat'])
INFO:relative:No unknown forces.
INFO:relative:Nonbonded method to be used (i.e. from old system): 4
INFO:relative:Adding and mapping old atoms to hybrid system...
INFO:relative:Adding and mapping new atoms to hybrid system...
INFO:relative:Added MonteCarloBarostat.
INFO:relative:getDefaultPeriodicBoxVectors added to hybrid: [Quantity(value=Vec3(x=6.9997, y=0.0, z=0.0), unit=nanometer), Quantity(value=Vec3(x=0.0, y=6.9997, z=0.0), unit=nanometer), Quantity(value=Vec3(x=0.0, y=0.0, z=6.9997), unit=nanometer)]
INFO:relative:Determined atom classes.
INFO:relative:Generating old system exceptions 

conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA
			HarmonicBondForce: 189.69655643562666
			HarmonicAngleForce: 791.7773839676565
			PeriodicTorsionForce: 3830.521840699088
			NonbondedForce: -63845.57749503781
			AndersenThermostat: 0.0
			MonteCarloBarostat: 0.0
conducting subsequent work with the following platform: CUDA
			CustomBondForce: 2.1615893092580074
			HarmonicBondForce: 187.53496712636868
			CustomAngleForce: 7.010010185642728
			HarmonicAngleForce: 787.3982850143808
			CustomTorsionForce: 0.05019711857836469
			PeriodicTorsionForce: 3830.698581808163
			NonbondedForce: -63764.01176366278
			CustomNonbondedForce: -76.72277237007906
			CustomBondForce: 0.0
			AndersenThermostat: 0.0
			MonteCarloBarostat: 0.0
conducting subsequent work with the following platform: CUDA
			CustomBondForce: 2.1615893092580074
			HarmonicBondForce: 187.53496712636868
			CustomAngleForce: 7.010010185642728
			HarmonicAng

In [62]:
htfs_t = [solvent_delivery.get_apo_htf(), solvent_delivery.get_complex_htf()]

In [63]:
top_old = md.Topology.from_openmm(htfs_t[0]._topology_proposal.old_topology)
top_new = md.Topology.from_openmm(htfs_t[0]._topology_proposal.new_topology)
traj = md.Trajectory(np.array(htfs_t[0].old_positions(htfs_t[0].hybrid_positions)), top_old)
traj.save("apo_old.pdb")
traj = md.Trajectory(np.array(htfs_t[0].new_positions(htfs_t[0].hybrid_positions)), top_new)
traj.save("apo_new.pdb")

top_old = md.Topology.from_openmm(htfs_t[1]._topology_proposal.old_topology)
top_new = md.Topology.from_openmm(htfs_t[1]._topology_proposal.new_topology)
traj = md.Trajectory(np.array(htfs_t[1].old_positions(htfs_t[1].hybrid_positions)), top_old)
traj.save("complex_old.pdb")
traj = md.Trajectory(np.array(htfs_t[1].new_positions(htfs_t[1].hybrid_positions)), top_new)
traj.save("complex_new.pdb")

#### Test solvation args, check that validate_endstates is passing

In [1]:
# Set up logger
import logging
_logger = logging.getLogger()
_logger.setLevel(logging.DEBUG)

In [2]:
# Solvent
from perses.app.relative_point_mutation_setup import PointMutationExecutor
from simtk import unit
solvent_delivery = PointMutationExecutor("../input/mmc2_barstar.pdb", 
                        '1', # First chain is the barstar one
                        '42', 
                        'ALA',
                        ligand_file="../input/mmc2_barnase.pdb",
                        ionic_strength=0.05*unit.molar
                       )




INFO:numexpr.utils:Note: detected 72 virtual cores but NumExpr set to maximum of 64, check "NUMEXPR_MAX_THREADS" environment variable.
INFO:numexpr.utils:Note: NumExpr detected 72 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
INFO:numexpr.utils:NumExpr defaulting to 8 threads.
RDKit WARNING: [11:10:45] Enabling RDKit 2019.09.3 jupyter extensions
INFO:root:solvating at 0.05 M using tip3p
INFO:root:solvating at 0.05 M using tip3p
INFO:proposal_generator:	Conducting polymer point mutation proposal...
INFO:proposal_generator:Using matching_criterion to chose best atom map
INFO:proposal_generator:Scaffold has symmetry of 0
INFO:proposal_generator:len [{4: 4, 7: 9}, {4: 4, 8: 9}, {4: 4, 9: 9}]
INFO:proposal_generator:{4: 4, 7: 9}
INFO:proposal_generator:{4: 4, 8: 9}
INFO:proposal_generator:{4: 4, 9: 9}
INFO:proposal_generator:Returning map that best satisfies matching_criterion
INFO:proposal_generator:Finding best map using matching_criterion name
INFO:proposal_gener

conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA


INFO:geometry:setting atoms_with_positions context new positions


conducting subsequent work with the following platform: CUDA


INFO:geometry:There are 2 new atoms
INFO:geometry:	reduced angle potential = 0.3940074113179214.
INFO:geometry:	reduced angle potential = 0.11304814424284342.
INFO:geometry:	beginning construction of no_nonbonded final system...
INFO:geometry:	initial no-nonbonded final system forces ['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce', 'MonteCarloBarostat']
INFO:geometry:	final no-nonbonded final system forces dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce'])
INFO:geometry:	there are 733 bond forces in the no-nonbonded final system
INFO:geometry:	there are 2628 angle forces in the no-nonbonded final system
INFO:geometry:	there are 4939 torsion forces in the no-nonbonded final system
INFO:geometry:forward final system defined with 0 neglected angles.


...

conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA


INFO:geometry:total reduced energy added from growth system: -64.43004096190329
INFO:geometry:final reduced energy 4736.681371796294
INFO:geometry:sum of energies: 4736.681372670266
INFO:geometry:magnitude of difference in the energies: 8.739719845607397e-07
INFO:geometry:Final logp_proposal: 33.161325460943324


added energy components: [('CustomBondForce', 0.09370408553241331), ('CustomAngleForce', 1.3102816193587339), ('CustomTorsionForce', 9.480381593867468), ('CustomBondForce', -75.31440826066189)]


INFO:relative:Beginning nonbonded method, total particle, barostat, and exceptions retrieval...
INFO:relative:Old system forces: dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce', 'MonteCarloBarostat'])
INFO:relative:New system forces: dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce', 'MonteCarloBarostat'])
INFO:relative:No unknown forces.
INFO:relative:Nonbonded method to be used (i.e. from old system): 4
INFO:relative:Adding and mapping old atoms to hybrid system...
INFO:relative:Adding and mapping new atoms to hybrid system...
INFO:relative:Added MonteCarloBarostat.
INFO:relative:getDefaultPeriodicBoxVectors added to hybrid: [Quantity(value=Vec3(x=6.7997, y=0.0, z=0.0), unit=nanometer), Quantity(value=Vec3(x=0.0, y=6.7997, z=0.0), unit=nanometer), Quantity(value=Vec3(x=0.0, y=0.0, z=6.7997), unit=nanometer)]
INFO:relative:Determined atom classes.
INFO:relative:Generating old system exceptions 

conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA
			HarmonicBondForce: 189.69655643562666
			HarmonicAngleForce: 791.7773839676565
			PeriodicTorsionForce: 3830.521840699088
			NonbondedForce: -24656.682861028956
			AndersenThermostat: 0.0
			MonteCarloBarostat: 0.0
conducting subsequent work with the following platform: CUDA
			CustomBondForce: 2.1615893092580074
			HarmonicBondForce: 187.53496712636868
			CustomAngleForce: 7.010010185642728
			HarmonicAngleForce: 789.5481394797692
			CustomTorsionForce: 0.05019711857836469
			PeriodicTorsionForce: 3830.5122690116996
			NonbondedForce: -24575.30011147004
			CustomNonbondedForce: -76.2693022951594
			CustomBondForce: 0.0
			AndersenThermostat: 0.0
			MonteCarloBarostat: 0.0
conducting subsequent work with the following platform: CUDA
			CustomBondForce: 2.1615893092580074
			HarmonicBondForce: 187.53496712636868
			CustomAngleForce: 7.010010185642728
			HarmonicAn

In [2]:
import pickle
import os
with open(os.path.join("/data/chodera/zhangi/perses_benchmark/neq/6/0/", f"{0}_{'apo'}.pickle"), 'rb') as f:
    htf = pickle.load(f)

In [4]:
import mdtraj as md
import numpy as np
top_new = md.Topology.from_openmm(htf._topology_proposal.new_topology)
traj = md.Trajectory(np.array(htf.new_positions(htf.hybrid_positions)), top_new)
traj.save("/data/chodera/zhangi/perses_benchmark/fah/mmc2_barstar_T42A.pdb")

## Y29A

#### Need to manually set validate_energy_bookkeeping to False

In [3]:
from perses.utils.openeye import *
from perses.annihilation.relative import HybridTopologyFactory
from perses.rjmc.topology_proposal import PointMutationEngine
from perses.rjmc.geometry import FFAllAngleGeometryEngine

import simtk.openmm as openmm
import simtk.openmm.app as app
import simtk.unit as unit
import numpy as np
from openmoltools import forcefield_generators
import copy
import mdtraj as md
from openmmtools.constants import kB
from perses.tests.utils import validate_endstate_energies
from openforcefield.topology import Molecule
from openmmforcefields.generators import SystemGenerator

In [4]:
ENERGY_THRESHOLD = 1e-2
temperature = 300 * unit.kelvin
kT = kB * temperature
beta = 1.0/kT

In [5]:
# First thing to do is load the apo protein to mutate...
protein_pdbfile = open("../input/mmc2_barstar.pdb", 'r')
protein_pdb = app.PDBFile(protein_pdbfile)
protein_pdbfile.close()
protein_positions, protein_topology, protein_md_topology = protein_pdb.positions, protein_pdb.topology, md.Topology.from_openmm(protein_pdb.topology)
protein_topology = protein_md_topology.to_openmm()
protein_n_atoms = protein_md_topology.n_atoms

In [6]:
# Load the ligand, if present
molecules = []
ligand_filename = "../input/mmc2_barnase.pdb"
if ligand_filename:
    if ligand_filename.endswith('.sdf'): # small molecule
        ligand_mol = createOEMolFromSDF(ligand_filename, index=ligand_index)
        ligand_mol = generate_unique_atom_names(ligand_mol)
        molecules.append(Molecule.from_openeye(ligand_mol, allow_undefined_stereo=False))
        ligand_positions, ligand_topology = extractPositionsFromOEMol(ligand_mol),  forcefield_generators.generateTopologyFromOEMol(ligand_mol)
        ligand_md_topology = md.Topology.from_openmm(ligand_topology)
        ligand_n_atoms = ligand_md_topology.n_atoms

    elif ligand_filename.endswith('pdb'): # protein
        ligand_pdbfile = open(ligand_filename, 'r')
        ligand_pdb = app.PDBFile(ligand_pdbfile)
        ligand_pdbfile.close()
        ligand_positions, ligand_topology, ligand_md_topology = ligand_pdb.positions, ligand_pdb.topology, md.Topology.from_openmm(
            ligand_pdb.topology)
        ligand_n_atoms = ligand_md_topology.n_atoms
    
    # Now create a complex
    complex_md_topology = protein_md_topology.join(ligand_md_topology)
    complex_topology = complex_md_topology.to_openmm()
    complex_positions = unit.Quantity(np.zeros([protein_n_atoms + ligand_n_atoms, 3]), unit=unit.nanometers)
    complex_positions[:protein_n_atoms, :] = protein_positions
    complex_positions[protein_n_atoms:, :] = ligand_positions

In [16]:
forcefield_files = ['amber14/protein.ff14SB.xml', 'amber14/tip3p.xml']
barostat = openmm.MonteCarloBarostat(1.0 * unit.atmosphere, 300 * unit.kelvin, 50)
forcefield_kwargs = {'removeCMMotion': False, 'ewaldErrorTolerance': 1e-4, 'constraints' : app.HBonds, 'hydrogenMass' : 4 * unit.amus}
periodic_forcefield_kwargs = {'nonbondedMethod': app.PME}
nonperiodic_forcefield_kwargs = None
system_generator = SystemGenerator(forcefields = forcefield_files,
                                                barostat=barostat,
                                                forcefield_kwargs=forcefield_kwargs,
                                                periodic_forcefield_kwargs=periodic_forcefield_kwargs,
                                   nonperiodic_forcefield_kwargs=nonperiodic_forcefield_kwargs,
                                                molecules=molecules,
                                                cache=None)

DEBUG:perses.forcefields.system_generators:Trying GAFFTemplateGenerator to load openff-1.0.0
DEBUG:perses.forcefields.system_generators:  GAFFTemplateGenerator cannot load openff-1.0.0
DEBUG:perses.forcefields.system_generators:Specified 'forcefield' (openff-1.0.0) must be one of ['gaff-1.4', 'gaff-1.8', 'gaff-1.81', 'gaff-2.1', 'gaff-2.11']
DEBUG:perses.forcefields.system_generators:Trying SMIRNOFFTemplateGenerator to load openff-1.0.0


In [10]:
def _solvate(topology,
                    positions,
                    model,
                    phase):
    """
    Generate a solvated topology, positions, and system for a given input topology and positions.
    For generating the system, the forcefield files provided in the constructor will be used.

    Parameters
    ----------
    topology : app.Topology
        Topology of the system to solvate
    positions : [n, 3] ndarray of Quantity nm
        the positions of the unsolvated system
    forcefield : SystemGenerator.forcefield
        forcefield file of solvent to add
    model : str, default 'tip3p'
        solvent model to use for solvation

    Returns
    -------
    solvated_topology : app.Topology
        Topology of the system with added waters
    solvated_positions : [n + 3(n_waters), 3] ndarray of Quantity nm
        Solvated positions
    solvated_system : openmm.System
        The parameterized system, containing a barostat if one was specified.
    """
    modeller = app.Modeller(topology, positions)


    # Now we have to add missing atoms
    if phase != 'vacuum':
        modeller.addSolvent(system_generator.forcefield, model=model, padding=1.0 * unit.nanometers, ionicStrength=0.05*unit.molar)
    else:
        pass

    solvated_topology = modeller.getTopology()
    solvated_positions = modeller.getPositions()

    # Canonicalize the solvated positions: turn tuples into np.array
    solvated_positions = unit.quantity.Quantity(value=np.array([list(atom_pos) for atom_pos in solvated_positions.value_in_unit_system(unit.md_unit_system)]), unit=unit.nanometers)
    solvated_system = system_generator.create_system(solvated_topology)

    return solvated_topology, solvated_positions, solvated_system


In [24]:
apo_input = list(_solvate(protein_topology, protein_positions, 'tip3p', phase='complex'))
inputs = [apo_input]
if ligand_filename:
    inputs.append(_solvate(complex_topology, complex_positions, 'tip3p', phase='complex'))

In [25]:
geometry_engine = FFAllAngleGeometryEngine(metadata=None,
                                                use_sterics=False,
                                                n_bond_divisions=100,
                                                n_angle_divisions=180,
                                                n_torsion_divisions=360,
                                                verbose=True,
                                                storage=None,
                                                bond_softening_constant=1.0,
                                                angle_softening_constant=1.0,
                                                neglect_angles = False,
                                                use_14_nonbondeds = True)

In [26]:
conduct_endstate_validation = True
htfs = []
for (top, pos, sys) in inputs:
    point_mutation_engine = PointMutationEngine(wildtype_topology=top,
                                                         system_generator=system_generator,
                                                         chain_id='1', # Denote the chain id allowed to mutate (it's always a string variable)
                                                         max_point_mutants=1,
                                                         residues_allowed_to_mutate=['29'], # The residue ids allowed to mutate
                                                         allowed_mutations=[('29', 'ALA')], # The residue ids allowed to mutate with the three-letter code allowed to change
                                                         aggregate=True) # Always allow aggregation

    topology_proposal = point_mutation_engine.propose(sys, top)

    new_positions, logp_proposal = geometry_engine.propose(topology_proposal, pos, beta, validate_energy_bookkeeping = False)
    logp_reverse = geometry_engine.logp_reverse(topology_proposal, new_positions, pos, beta, validate_energy_bookkeeping = False)

    forward_htf = HybridTopologyFactory(topology_proposal=topology_proposal,
                                         current_positions=pos,
                                         new_positions=new_positions,
                                         use_dispersion_correction=False,
                                         functions=None,
                                         softcore_alpha=None,
                                         bond_softening_constant=1.0,
                                         angle_softening_constant=1.0,
                                         soften_only_new=False,
                                         neglected_new_angle_terms=[],
                                         neglected_old_angle_terms=[],
                                         softcore_LJ_v2=True,
                                         softcore_electrostatics=True,
                                         softcore_LJ_v2_alpha=0.85,
                                         softcore_electrostatics_alpha=0.3,
                                         softcore_sigma_Q=1.0,
                                         interpolate_old_and_new_14s=False,
                                         omitted_terms=None)

    if not topology_proposal.unique_new_atoms:
        assert geometry_engine.forward_final_context_reduced_potential == None, f"There are no unique new atoms but the geometry_engine's final context reduced potential is not None (i.e. {self._geometry_engine.forward_final_context_reduced_potential})"
        assert geometry_engine.forward_atoms_with_positions_reduced_potential == None, f"There are no unique new atoms but the geometry_engine's forward atoms-with-positions-reduced-potential in not None (i.e. { self._geometry_engine.forward_atoms_with_positions_reduced_potential})"
        vacuum_added_valence_energy = 0.0
    else:
        added_valence_energy = geometry_engine.forward_final_context_reduced_potential - geometry_engine.forward_atoms_with_positions_reduced_potential

    if not topology_proposal.unique_old_atoms:
        assert geometry_engine.reverse_final_context_reduced_potential == None, f"There are no unique old atoms but the geometry_engine's final context reduced potential is not None (i.e. {self._geometry_engine.reverse_final_context_reduced_potential})"
        assert geometry_engine.reverse_atoms_with_positions_reduced_potential == None, f"There are no unique old atoms but the geometry_engine's atoms-with-positions-reduced-potential in not None (i.e. { self._geometry_engine.reverse_atoms_with_positions_reduced_potential})"
        subtracted_valence_energy = 0.0
    else:
        subtracted_valence_energy = geometry_engine.reverse_final_context_reduced_potential - geometry_engine.reverse_atoms_with_positions_reduced_potential


    if conduct_endstate_validation:
        zero_state_error, one_state_error = validate_endstate_energies(forward_htf._topology_proposal, forward_htf, added_valence_energy, subtracted_valence_energy, beta=beta, ENERGY_THRESHOLD=ENERGY_THRESHOLD)
        assert zero_state_error < ENERGY_THRESHOLD, f"Reduced potential difference of the nonalchemical and alchemical Lambda = 0 state is above the threshold ({ENERGY_THRESHOLD}): {zero_state_error}"
        assert one_state_error < ENERGY_THRESHOLD, f"Reduced potential difference of the nonalchemical and alchemical Lambda = 1 state is above the threshold ({ENERGY_THRESHOLD}): {one_state_error}"
    else:
        pass

    htfs.append(forward_htf)


INFO:proposal_generator:	Conducting polymer point mutation proposal...
INFO:proposal_generator:[3, 3, 3, 3, 3, 3]
INFO:proposal_generator:Maximum atom matched after hydrogen exceptions: 3
INFO:geometry:propose: performing forward proposal
INFO:geometry:propose: unique new atoms detected; proceeding to _logp_propose...
INFO:geometry:Conducting forward proposal...
INFO:geometry:Computing proposal order with NetworkX...
INFO:geometry:number of atoms to be placed: 1
INFO:geometry:Atom index proposal order is [474]
INFO:geometry:omitted_bonds: []
INFO:geometry:direction of proposal is forward; creating atoms_with_positions and new positions from old system/topology...
INFO:geometry:creating growth system...
INFO:geometry:	creating bond force...
INFO:geometry:	there are 727 bonds in reference force.
INFO:geometry:	creating angle force...
INFO:geometry:	there are 2616 angles in reference force.
INFO:geometry:	creating torsion force...
INFO:geometry:	creating extra torsions force...
INFO:geome

conducting subsequent work with the following platform: CUDA


INFO:geometry:setting atoms_with_positions context new positions


conducting subsequent work with the following platform: CUDA


INFO:geometry:There are 1 new atoms
INFO:geometry:	reduced angle potential = 0.11817194896911984.
INFO:geometry:	beginning construction of no_nonbonded final system...
INFO:geometry:	initial no-nonbonded final system forces ['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce', 'MonteCarloBarostat']
INFO:geometry:	final no-nonbonded final system forces dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce'])
INFO:geometry:	there are 727 bond forces in the no-nonbonded final system
INFO:geometry:	there are 2616 angle forces in the no-nonbonded final system
INFO:geometry:	there are 4925 torsion forces in the no-nonbonded final system
INFO:geometry:forward final system defined with 0 neglected angles.


...

conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA


INFO:geometry:total reduced energy added from growth system: -4.930837145159151
INFO:geometry:final reduced energy 4799.418046758731
INFO:geometry:sum of energies: 4801.474758057833
INFO:geometry:magnitude of difference in the energies: 2.056711299101787
INFO:geometry:Final logp_proposal: 96.71409278987517


added energy components: [('CustomBondForce', 0.5394473613996584), ('CustomAngleForce', 0.7356180484576128), ('CustomTorsionForce', 3.547716587135036), ('CustomBondForce', -9.753619142151456)]


INFO:relative:Beginning nonbonded method, total particle, barostat, and exceptions retrieval...
INFO:relative:Old system forces: dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce', 'MonteCarloBarostat'])
INFO:relative:New system forces: dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce', 'MonteCarloBarostat'])
INFO:relative:No unknown forces.
INFO:relative:Nonbonded method to be used (i.e. from old system): 4
INFO:relative:Adding and mapping old atoms to hybrid system...
INFO:relative:Adding and mapping new atoms to hybrid system...
INFO:relative:Added MonteCarloBarostat.
INFO:relative:getDefaultPeriodicBoxVectors added to hybrid: [Quantity(value=Vec3(x=6.9997, y=0.0, z=0.0), unit=nanometer), Quantity(value=Vec3(x=0.0, y=6.9997, z=0.0), unit=nanometer), Quantity(value=Vec3(x=0.0, y=0.0, z=6.9997), unit=nanometer)]
INFO:relative:Determined atom classes.
INFO:relative:Generating old system exceptions 

conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA
			HarmonicBondForce: 189.69655643562666
			HarmonicAngleForce: 791.7773839676565
			PeriodicTorsionForce: 3830.521840699088
			NonbondedForce: -64686.8115942554
			AndersenThermostat: 0.0
			MonteCarloBarostat: 0.0
conducting subsequent work with the following platform: CUDA
			CustomBondForce: 3.1285080029054586
			HarmonicBondForce: 186.5680484327212
			CustomAngleForce: 8.414175953372672
			HarmonicAngleForce: 786.5369724394424
			CustomTorsionForce: 0.05405409160040507
			PeriodicTorsionForce: 3830.5673138964153
			NonbondedForce: -64574.529923352966
			CustomNonbondedForce: -109.25558953092498
			CustomBondForce: 0.0
			AndersenThermostat: 0.0
			MonteCarloBarostat: 0.0
conducting subsequent work with the following platform: CUDA
			CustomBondForce: 3.1285080029054586
			HarmonicBondForce: 186.5680484327212
			CustomAngleForce: 8.414175953372672
			HarmonicAng

In [27]:
pickle.dump(htfs[0], open("Y29A_apo.pickle", "wb" ))
pickle.dump(htfs[1], open("Y29A_complex.pickle", "wb" ))


In [28]:
top_old = md.Topology.from_openmm(htfs[0]._topology_proposal.old_topology)
top_new = md.Topology.from_openmm(htfs[0]._topology_proposal.new_topology)
traj = md.Trajectory(np.array(htfs[0].old_positions(htfs[0].hybrid_positions)), top_old)
traj.save("apo_old.pdb")
traj = md.Trajectory(np.array(htfs[0].new_positions(htfs[0].hybrid_positions)), top_new)
traj.save("apo_new.pdb")

top_old = md.Topology.from_openmm(htfs[1]._topology_proposal.old_topology)
top_new = md.Topology.from_openmm(htfs[1]._topology_proposal.new_topology)
traj = md.Trajectory(np.array(htfs[1].old_positions(htfs[1].hybrid_positions)), top_old)
traj.save("complex_old.pdb")
traj = md.Trajectory(np.array(htfs[1].new_positions(htfs[1].hybrid_positions)), top_new)
traj.save("complex_new.pdb")

#### Check that the permanent fix for validate_energy_bookeeping works

In [3]:
ENERGY_THRESHOLD = 1e-2
temperature = 300 * unit.kelvin
kT = kB * temperature
beta = 1.0/kT

In [4]:

from perses.app.relative_point_mutation_setup import PointMutationExecutor
class PointMutationExecutor2(PointMutationExecutor):
    def __init__(self,
                 protein_filename,
                 mutation_chain_id,
                 mutation_residue_id,
                 proposed_residue,
                 phase='complex',
                 conduct_endstate_validation=True,
                 ligand_filename=None,
                 ligand_index=0,
                 forcefield_files=['amber14/protein.ff14SB.xml', 'amber14/tip3p.xml'],
                 barostat=openmm.MonteCarloBarostat(1.0 * unit.atmosphere, temperature, 50),
                 forcefield_kwargs={'removeCMMotion': False, 'ewaldErrorTolerance': 1e-4, 'constraints' : app.HBonds, 'hydrogenMass' : 4 * unit.amus},
                 periodic_forcefield_kwargs={'nonbondedMethod': app.PME},
                 nonperiodic_forcefield_kwargs=None,
                 small_molecule_forcefields='gaff-2.11',
                 **kwargs):
            super().__init__(
                 protein_filename,
                 mutation_chain_id,
                 mutation_residue_id,
                 proposed_residue,
                 phase='complex',
                 conduct_endstate_validation=True,
                 ligand_filename=ligand_filename,
                 ligand_index=0,
                 forcefield_files=['amber14/protein.ff14SB.xml', 'amber14/tip3p.xml'],
                 barostat=openmm.MonteCarloBarostat(1.0 * unit.atmosphere, temperature, 50),
                 forcefield_kwargs={'removeCMMotion': False, 'ewaldErrorTolerance': 1e-4, 'constraints' : app.HBonds, 'hydrogenMass' : 4 * unit.amus},
                 periodic_forcefield_kwargs={'nonbondedMethod': app.PME},
                 nonperiodic_forcefield_kwargs=None,
                 small_molecule_forcefields='gaff-2.11')
            print(ligand_filename)
    def _solvate(self,
                    topology,
                    positions,
                    model,
                    phase):
        """
        Generate a solvated topology, positions, and system for a given input topology and positions.
        For generating the system, the forcefield files provided in the constructor will be used.

        Parameters
        ----------
        topology : app.Topology
            Topology of the system to solvate
        positions : [n, 3] ndarray of Quantity nm
            the positions of the unsolvated system
        forcefield : SystemGenerator.forcefield
            forcefield file of solvent to add
        model : str, default 'tip3p'
            solvent model to use for solvation

        Returns
        -------
        solvated_topology : app.Topology
            Topology of the system with added waters
        solvated_positions : [n + 3(n_waters), 3] ndarray of Quantity nm
            Solvated positions
        solvated_system : openmm.System
            The parameterized system, containing a barostat if one was specified.
        """
        print("using override solvate function")
        modeller = app.Modeller(topology, positions)


        # Now we have to add missing atoms
        if phase != 'vacuum':
            modeller.addSolvent(self.system_generator.forcefield, model=model, padding=1.0 * unit.nanometers, ionicStrength=0.05*unit.molar)
        else:
            pass

        solvated_topology = modeller.getTopology()
        solvated_positions = modeller.getPositions()

        # Canonicalize the solvated positions: turn tuples into np.array
        solvated_positions = unit.quantity.Quantity(value=np.array([list(atom_pos) for atom_pos in solvated_positions.value_in_unit_system(unit.md_unit_system)]), unit=unit.nanometers)
        solvated_system = self.system_generator.create_system(solvated_topology)

        return solvated_topology, solvated_positions, solvated_system


In [5]:
# Solvent

solvent_delivery = PointMutationExecutor2("../input/mmc2_barstar.pdb", 
                        '1', # First chain is the barstar one
                        '29', 
                        'ALA',
                        ligand_filename="../input/mmc2_barnase.pdb",
                       )




DEBUG:perses.forcefields.system_generators:Trying GAFFTemplateGenerator to load gaff-2.11


using override solvate function
using override solvate function


INFO:proposal_generator:	Conducting polymer point mutation proposal...
INFO:proposal_generator:[3, 3, 3, 3, 3, 3]
INFO:proposal_generator:Maximum atom matched after hydrogen exceptions: 3
INFO:geometry:propose: performing forward proposal
INFO:geometry:propose: unique new atoms detected; proceeding to _logp_propose...
INFO:geometry:Conducting forward proposal...
INFO:geometry:Computing proposal order with NetworkX...
INFO:geometry:number of atoms to be placed: 1
INFO:geometry:Atom index proposal order is [474]
INFO:geometry:omitted_bonds: []
INFO:geometry:direction of proposal is forward; creating atoms_with_positions and new positions from old system/topology...
INFO:geometry:creating growth system...
INFO:geometry:	creating bond force...
INFO:geometry:	there are 727 bonds in reference force.
INFO:geometry:	creating angle force...
INFO:geometry:	there are 2616 angles in reference force.
INFO:geometry:	creating torsion force...
INFO:geometry:	creating extra torsions force...
INFO:geome

conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA


INFO:geometry:setting atoms_with_positions context new positions


...

conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA


INFO:geometry:total reduced energy added from growth system: -4.930837145159151
INFO:geometry:final reduced energy 4799.418046758731
INFO:geometry:sum of energies: 4801.474758057833
INFO:geometry:magnitude of difference in the energies: 2.056711299101787
INFO:geometry:Final logp_proposal: 94.88114425478453


added energy components: [('CustomBondForce', 0.5394473613996584), ('CustomAngleForce', 0.7356180484576128), ('CustomTorsionForce', 3.547716587135036), ('CustomBondForce', -9.753619142151456)]


INFO:relative:Beginning nonbonded method, total particle, barostat, and exceptions retrieval...
INFO:relative:Old system forces: dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce', 'MonteCarloBarostat'])
INFO:relative:New system forces: dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce', 'MonteCarloBarostat'])
INFO:relative:No unknown forces.
INFO:relative:Nonbonded method to be used (i.e. from old system): 4
INFO:relative:Adding and mapping old atoms to hybrid system...
INFO:relative:Adding and mapping new atoms to hybrid system...
INFO:relative:Added MonteCarloBarostat.
INFO:relative:getDefaultPeriodicBoxVectors added to hybrid: [Quantity(value=Vec3(x=6.9997, y=0.0, z=0.0), unit=nanometer), Quantity(value=Vec3(x=0.0, y=6.9997, z=0.0), unit=nanometer), Quantity(value=Vec3(x=0.0, y=0.0, z=6.9997), unit=nanometer)]
INFO:relative:Determined atom classes.
INFO:relative:Generating old system exceptions 

conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA
			HarmonicBondForce: 189.69655643562666
			HarmonicAngleForce: 791.7773839676565
			PeriodicTorsionForce: 3830.521840699088
			NonbondedForce: -64671.092819262194
			AndersenThermostat: 0.0
			MonteCarloBarostat: 0.0
conducting subsequent work with the following platform: CUDA
			CustomBondForce: 3.1285080029054586
			HarmonicBondForce: 186.5680484327212
			CustomAngleForce: 8.414175953372672
			HarmonicAngleForce: 783.8044312136803
			CustomTorsionForce: 0.05405409160040507
			PeriodicTorsionForce: 3830.4814978474174
			NonbondedForce: -64559.14493831984
			CustomNonbondedForce: -109.25558953092498
			CustomBondForce: 0.0
			AndersenThermostat: 0.0
			MonteCarloBarostat: 0.0
conducting subsequent work with the following platform: CUDA
			CustomBondForce: 3.1285080029054586
			HarmonicBondForce: 186.5680484327212
			CustomAngleForce: 8.414175953372672
			HarmonicAn

In [6]:
htfs_t = [solvent_delivery.get_apo_htf(), solvent_delivery.get_complex_htf()]

In [7]:
top_old = md.Topology.from_openmm(htfs_t[0]._topology_proposal.old_topology)
top_new = md.Topology.from_openmm(htfs_t[0]._topology_proposal.new_topology)
traj = md.Trajectory(np.array(htfs_t[0].old_positions(htfs_t[0].hybrid_positions)), top_old)
traj.save("apo_old.pdb")
traj = md.Trajectory(np.array(htfs_t[0].new_positions(htfs_t[0].hybrid_positions)), top_new)
traj.save("apo_new.pdb")

top_old = md.Topology.from_openmm(htfs_t[1]._topology_proposal.old_topology)
top_new = md.Topology.from_openmm(htfs_t[1]._topology_proposal.new_topology)
traj = md.Trajectory(np.array(htfs_t[1].old_positions(htfs_t[1].hybrid_positions)), top_old)
traj.save("complex_old.pdb")
traj = md.Trajectory(np.array(htfs_t[1].new_positions(htfs_t[1].hybrid_positions)), top_new)
traj.save("complex_new.pdb")

In [5]:
import pickle
with open(os.path.join("/data/chodera/zhangi/perses_benchmark/neq/6/1/", f"{1}_{'apo'}.pickle"), 'rb') as f:
    htf = pickle.load(f)

In [12]:
for res in htf._topology_proposal.new_topology.residues():
    print(res, res.id, res.insertionCode)

<Residue 0 (ACE) of chain 0> 0 
<Residue 1 (LYS) of chain 0> 1 
<Residue 2 (LYS) of chain 0> 2 
<Residue 3 (ALA) of chain 0> 3 
<Residue 4 (VAL) of chain 0> 4 
<Residue 5 (ILE) of chain 0> 5 
<Residue 6 (ASN) of chain 0> 6 
<Residue 7 (GLY) of chain 0> 7 
<Residue 8 (GLU) of chain 0> 8 
<Residue 9 (GLN) of chain 0> 9 
<Residue 10 (ILE) of chain 0> 10 
<Residue 11 (ARG) of chain 0> 11 
<Residue 12 (SER) of chain 0> 12 
<Residue 13 (ILE) of chain 0> 13 
<Residue 14 (SER) of chain 0> 14 
<Residue 15 (ASP) of chain 0> 15 
<Residue 16 (LEU) of chain 0> 16 
<Residue 17 (HIS) of chain 0> 17 
<Residue 18 (GLN) of chain 0> 18 
<Residue 19 (THR) of chain 0> 19 
<Residue 20 (LEU) of chain 0> 20 
<Residue 21 (LYS) of chain 0> 21 
<Residue 22 (LYS) of chain 0> 22 
<Residue 23 (GLU) of chain 0> 23 
<Residue 24 (LEU) of chain 0> 24 
<Residue 25 (ALA) of chain 0> 25 
<Residue 26 (LEU) of chain 0> 26 
<Residue 27 (PRO) of chain 0> 27 
<Residue 28 (GLU) of chain 0> 28 
<Residue 29 (ALA) of chain 0> 29 


<Residue 611 (HOH) of chain 2> 614 
<Residue 612 (HOH) of chain 2> 615 
<Residue 613 (HOH) of chain 2> 616 
<Residue 614 (HOH) of chain 2> 617 
<Residue 615 (HOH) of chain 2> 618 
<Residue 616 (HOH) of chain 2> 619 
<Residue 617 (HOH) of chain 2> 620 
<Residue 618 (HOH) of chain 2> 621 
<Residue 619 (HOH) of chain 2> 622 
<Residue 620 (HOH) of chain 2> 623 
<Residue 621 (HOH) of chain 2> 624 
<Residue 622 (HOH) of chain 2> 625 
<Residue 623 (HOH) of chain 2> 626 
<Residue 624 (HOH) of chain 2> 627 
<Residue 625 (HOH) of chain 2> 628 
<Residue 626 (HOH) of chain 2> 629 
<Residue 627 (HOH) of chain 2> 630 
<Residue 628 (HOH) of chain 2> 631 
<Residue 629 (HOH) of chain 2> 632 
<Residue 630 (HOH) of chain 2> 633 
<Residue 631 (HOH) of chain 2> 634 
<Residue 632 (HOH) of chain 2> 635 
<Residue 633 (HOH) of chain 2> 636 
<Residue 634 (HOH) of chain 2> 637 
<Residue 635 (HOH) of chain 2> 638 
<Residue 636 (HOH) of chain 2> 639 
<Residue 637 (HOH) of chain 2> 640 
<Residue 638 (HOH) of chain 

<Residue 1622 (HOH) of chain 2> 1629 
<Residue 1623 (HOH) of chain 2> 1630 
<Residue 1624 (HOH) of chain 2> 1631 
<Residue 1625 (HOH) of chain 2> 1632 
<Residue 1626 (HOH) of chain 2> 1633 
<Residue 1627 (HOH) of chain 2> 1634 
<Residue 1628 (HOH) of chain 2> 1635 
<Residue 1629 (HOH) of chain 2> 1636 
<Residue 1630 (HOH) of chain 2> 1637 
<Residue 1631 (HOH) of chain 2> 1638 
<Residue 1632 (HOH) of chain 2> 1639 
<Residue 1633 (HOH) of chain 2> 1640 
<Residue 1634 (HOH) of chain 2> 1641 
<Residue 1635 (HOH) of chain 2> 1642 
<Residue 1636 (HOH) of chain 2> 1643 
<Residue 1637 (HOH) of chain 2> 1644 
<Residue 1638 (HOH) of chain 2> 1645 
<Residue 1639 (HOH) of chain 2> 1646 
<Residue 1640 (HOH) of chain 2> 1647 
<Residue 1641 (HOH) of chain 2> 1648 
<Residue 1642 (HOH) of chain 2> 1649 
<Residue 1643 (HOH) of chain 2> 1650 
<Residue 1644 (HOH) of chain 2> 1651 
<Residue 1645 (HOH) of chain 2> 1652 
<Residue 1646 (HOH) of chain 2> 1653 
<Residue 1647 (HOH) of chain 2> 1654 
<Residue 164

<Residue 2622 (HOH) of chain 2> 2637 
<Residue 2623 (HOH) of chain 2> 2638 
<Residue 2624 (HOH) of chain 2> 2639 
<Residue 2625 (HOH) of chain 2> 2640 
<Residue 2626 (HOH) of chain 2> 2641 
<Residue 2627 (HOH) of chain 2> 2642 
<Residue 2628 (HOH) of chain 2> 2643 
<Residue 2629 (HOH) of chain 2> 2644 
<Residue 2630 (HOH) of chain 2> 2645 
<Residue 2631 (HOH) of chain 2> 2646 
<Residue 2632 (HOH) of chain 2> 2647 
<Residue 2633 (HOH) of chain 2> 2648 
<Residue 2634 (HOH) of chain 2> 2649 
<Residue 2635 (HOH) of chain 2> 2650 
<Residue 2636 (HOH) of chain 2> 2651 
<Residue 2637 (HOH) of chain 2> 2652 
<Residue 2638 (HOH) of chain 2> 2653 
<Residue 2639 (HOH) of chain 2> 2654 
<Residue 2640 (HOH) of chain 2> 2655 
<Residue 2641 (HOH) of chain 2> 2656 
<Residue 2642 (HOH) of chain 2> 2657 
<Residue 2643 (HOH) of chain 2> 2658 
<Residue 2644 (HOH) of chain 2> 2659 
<Residue 2645 (HOH) of chain 2> 2660 
<Residue 2646 (HOH) of chain 2> 2661 
<Residue 2647 (HOH) of chain 2> 2662 
<Residue 264

<Residue 3622 (HOH) of chain 2> 3643 
<Residue 3623 (HOH) of chain 2> 3644 
<Residue 3624 (HOH) of chain 2> 3645 
<Residue 3625 (HOH) of chain 2> 3646 
<Residue 3626 (HOH) of chain 2> 3647 
<Residue 3627 (HOH) of chain 2> 3648 
<Residue 3628 (HOH) of chain 2> 3649 
<Residue 3629 (HOH) of chain 2> 3650 
<Residue 3630 (HOH) of chain 2> 3651 
<Residue 3631 (HOH) of chain 2> 3652 
<Residue 3632 (HOH) of chain 2> 3653 
<Residue 3633 (HOH) of chain 2> 3654 
<Residue 3634 (HOH) of chain 2> 3655 
<Residue 3635 (HOH) of chain 2> 3656 
<Residue 3636 (HOH) of chain 2> 3657 
<Residue 3637 (HOH) of chain 2> 3658 
<Residue 3638 (HOH) of chain 2> 3659 
<Residue 3639 (HOH) of chain 2> 3660 
<Residue 3640 (HOH) of chain 2> 3661 
<Residue 3641 (HOH) of chain 2> 3662 
<Residue 3642 (HOH) of chain 2> 3663 
<Residue 3643 (HOH) of chain 2> 3664 
<Residue 3644 (HOH) of chain 2> 3665 
<Residue 3645 (HOH) of chain 2> 3666 
<Residue 3646 (HOH) of chain 2> 3667 
<Residue 3647 (HOH) of chain 2> 3668 
<Residue 364

<Residue 4621 (HOH) of chain 2> 4651 
<Residue 4622 (HOH) of chain 2> 4652 
<Residue 4623 (HOH) of chain 2> 4653 
<Residue 4624 (HOH) of chain 2> 4654 
<Residue 4625 (HOH) of chain 2> 4655 
<Residue 4626 (HOH) of chain 2> 4656 
<Residue 4627 (HOH) of chain 2> 4657 
<Residue 4628 (HOH) of chain 2> 4658 
<Residue 4629 (HOH) of chain 2> 4659 
<Residue 4630 (HOH) of chain 2> 4660 
<Residue 4631 (HOH) of chain 2> 4661 
<Residue 4632 (HOH) of chain 2> 4662 
<Residue 4633 (HOH) of chain 2> 4663 
<Residue 4634 (HOH) of chain 2> 4664 
<Residue 4635 (HOH) of chain 2> 4665 
<Residue 4636 (HOH) of chain 2> 4666 
<Residue 4637 (HOH) of chain 2> 4667 
<Residue 4638 (HOH) of chain 2> 4668 
<Residue 4639 (HOH) of chain 2> 4669 
<Residue 4640 (HOH) of chain 2> 4670 
<Residue 4641 (HOH) of chain 2> 4671 
<Residue 4642 (HOH) of chain 2> 4672 
<Residue 4643 (HOH) of chain 2> 4673 
<Residue 4644 (HOH) of chain 2> 4674 
<Residue 4645 (HOH) of chain 2> 4675 
<Residue 4646 (HOH) of chain 2> 4676 
<Residue 464

In [6]:
top_new = md.Topology.from_openmm(htf._topology_proposal.new_topology)
traj = md.Trajectory(np.array(htf.new_positions(htf.hybrid_positions)), top_new)
traj.save("/data/chodera/zhangi/perses_benchmark/fah/mmc2_barstar_Y29A.pdb")

## W38F

In [6]:
# Set up logger
import logging
_logger = logging.getLogger()
_logger.setLevel(logging.DEBUG)

In [7]:
# Solvent
from perses.app.relative_point_mutation_setup import PointMutationExecutor
from simtk import unit
solvent_delivery = PointMutationExecutor("../input/mmc2_barstar.pdb", 
                        '1', # First chain is the barstar one
                        '38', 
                        'PHE',
                        ligand_file="../input/mmc2_barnase.pdb",
                        ionic_strength=0.05*unit.molar
                       )




DEBUG:perses.forcefields.system_generators:Trying GAFFTemplateGenerator to load gaff-2.11
INFO:root:solvating at 0.05 M using tip3p
INFO:root:solvating at 0.05 M using tip3p
INFO:proposal_generator:	Conducting polymer point mutation proposal...
INFO:proposal_generator:Using matching_criterion to chose best atom map
INFO:proposal_generator:Scaffold has symmetry of 0
INFO:proposal_generator:len [{4: 4, 5: 5, 7: 6, 6: 7, 8: 9, 9: 10, 10: 12, 13: 16, 14: 17, 16: 18, 18: 19, 17: 20, 19: 22}, {4: 4, 5: 5, 6: 6, 7: 7, 9: 9, 8: 10, 10: 12, 13: 16, 14: 17, 15: 18, 17: 19, 18: 20, 19: 22}, {4: 4, 5: 5, 7: 6, 6: 7, 8: 9, 10: 12, 9: 13, 14: 16, 13: 17, 16: 18, 17: 20, 19: 22, 18: 23}, {4: 4, 5: 5, 6: 6, 7: 7, 9: 9, 10: 12, 8: 13, 14: 16, 13: 17, 15: 18, 18: 20, 19: 22, 17: 23}, {4: 4, 5: 5, 6: 6, 10: 8, 8: 10, 9: 11, 7: 13, 14: 16, 13: 17, 15: 18, 17: 19, 18: 21, 16: 23}, {4: 4, 5: 5, 7: 6, 10: 8, 9: 10, 8: 11, 6: 13, 14: 16, 13: 17, 16: 18, 18: 19, 17: 21, 15: 23}, {4: 4, 5: 5, 6: 7, 8: 9, 7: 11,

conducting subsequent work with the following platform: CUDA


INFO:geometry:setting atoms_with_positions context new positions


conducting subsequent work with the following platform: CUDA


INFO:geometry:There are 14 new atoms
INFO:geometry:	reduced angle potential = 0.08055741036048245.
INFO:geometry:	reduced angle potential = 0.8773033236291364.
INFO:geometry:	reduced angle potential = 7.031691584180479e-05.
INFO:geometry:	reduced angle potential = 0.8544343782855056.
INFO:geometry:	reduced angle potential = 0.35945959884672257.
INFO:geometry:	reduced angle potential = 0.19959197191860056.
INFO:geometry:	reduced angle potential = 0.1416182754972578.
INFO:geometry:	reduced angle potential = 0.3735234113690808.
INFO:geometry:	reduced angle potential = 2.298358507628671.
INFO:geometry:	reduced angle potential = 0.37694720482073396.
INFO:geometry:	reduced angle potential = 0.3805053254791052.
INFO:geometry:	reduced angle potential = 0.11325002195218778.
INFO:geometry:	reduced angle potential = 0.20944145799616798.
INFO:geometry:	reduced angle potential = 0.16316051332241796.
INFO:geometry:	beginning construction of no_nonbonded final system...
INFO:geometry:	initial no-nonb

...

INFO:geometry:total reduced energy added from growth system: 45.11436836205859
INFO:geometry:final reduced energy 4849.210695559174
INFO:geometry:sum of energies: 4844.687412607537
INFO:geometry:magnitude of difference in the energies: 4.52328295163705
INFO:geometry:Final logp_proposal: 143.4314241285523


added energy components: [('CustomBondForce', 0.3285643943424474), ('CustomAngleForce', 2.49314072549162), ('CustomTorsionForce', 9.329865478932332), ('CustomBondForce', 32.96279776329221)]


INFO:relative:Beginning nonbonded method, total particle, barostat, and exceptions retrieval...
INFO:relative:Old system forces: dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce', 'MonteCarloBarostat'])
INFO:relative:New system forces: dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce', 'MonteCarloBarostat'])
INFO:relative:No unknown forces.
INFO:relative:Nonbonded method to be used (i.e. from old system): 4
INFO:relative:Adding and mapping old atoms to hybrid system...
INFO:relative:Adding and mapping new atoms to hybrid system...
INFO:relative:Added MonteCarloBarostat.
INFO:relative:getDefaultPeriodicBoxVectors added to hybrid: [Quantity(value=Vec3(x=6.7997, y=0.0, z=0.0), unit=nanometer), Quantity(value=Vec3(x=0.0, y=6.7997, z=0.0), unit=nanometer), Quantity(value=Vec3(x=0.0, y=0.0, z=6.7997), unit=nanometer)]
INFO:relative:Determined atom classes.
INFO:relative:Generating old system exceptions 

conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA
			HarmonicBondForce: 189.69655643562666
			HarmonicAngleForce: 791.7773839676565
			PeriodicTorsionForce: 3830.521840699088
			NonbondedForce: -24597.255196241607
			AndersenThermostat: 0.0
			MonteCarloBarostat: 0.0
conducting subsequent work with the following platform: CUDA
			CustomBondForce: 1.4547738181404877
			HarmonicBondForce: 193.57830561031327
			CustomAngleForce: 6.333342345896989
			HarmonicAngleForce: 816.5668833554389
			CustomTorsionForce: 0.031604783178227
			PeriodicTorsionForce: 3851.074454578621
			NonbondedForce: -24465.422313627307
			CustomNonbondedForce: -118.48097691287649
			CustomBondForce: 0.0
			AndersenThermostat: 0.0
			MonteCarloBarostat: 0.0
conducting subsequent work with the following platform: CUDA
			CustomBondForce: 1.4547738181404877
			HarmonicBondForce: 193.57830561031327
			CustomAngleForce: 6.333342345896989
			HarmonicAn

			HarmonicBondForce: 194.68970781955804
			HarmonicAngleForce: 820.168847250155
			PeriodicTorsionForce: 3841.7577612937757
			NonbondedForce: 1645314.9230321397
			AndersenThermostat: 0.0
			MonteCarloBarostat: 0.0


In [3]:
def render_protein_residue_atom_mapping(topology_proposal, filename):
    """
    wrap the `render_atom_mapping` method around protein point mutation topologies.
    TODO : make modification to `render_atom_mapping` so that the backbone atoms are not written in the output.
    
    arguments
        topology_proposal : perses.rjmc.topology_proposal.TopologyProposal object
            topology proposal of protein mutation
        filename : str
            filename to write the map
    """
    from perses.utils.smallmolecules import render_atom_mapping
    oe_res_maps = {}
    for omm_new_idx, omm_old_idx in topology_proposal._new_to_old_atom_map.items():
        if omm_new_idx in topology_proposal._new_topology.residue_to_oemol_map.keys():
            try:
                oe_res_maps[topology_proposal._new_topology.residue_to_oemol_map[omm_new_idx]] = topology_proposal._old_topology.residue_to_oemol_map[omm_old_idx]
            except:
                pass
            
    render_atom_mapping(filename, topology_proposal._old_topology.residue_oemol, topology_proposal._new_topology.residue_oemol, oe_res_maps)
    

In [4]:
render_protein_residue_atom_mapping(solvent_delivery.get_apo_htf()._topology_proposal, "map.png")

In [5]:
import pickle
import os
out_dir = '/data/chodera/zhangi/perses_benchmark/neq/6/'
pickle.dump(solvent_delivery.get_apo_htf(), open(os.path.join(out_dir, "2/2_apo.pickle"), "wb" ))
pickle.dump(solvent_delivery.get_complex_htf(), open(os.path.join(out_dir, "2/2_complex.pickle"), "wb" ))


In [8]:
import mdtraj as md
import numpy as np
htfs_t = [solvent_delivery.get_apo_htf(), solvent_delivery.get_complex_htf()]

top_old = md.Topology.from_openmm(htfs_t[0]._topology_proposal.old_topology)
top_new = md.Topology.from_openmm(htfs_t[0]._topology_proposal.new_topology)
traj = md.Trajectory(np.array(htfs_t[0].old_positions(htfs_t[0].hybrid_positions)), top_old)
traj.save("2_apo_old.pdb")
traj = md.Trajectory(np.array(htfs_t[0].new_positions(htfs_t[0].hybrid_positions)), top_new)
traj.save("2_apo_new.pdb")

top_old = md.Topology.from_openmm(htfs_t[1]._topology_proposal.old_topology)
top_new = md.Topology.from_openmm(htfs_t[1]._topology_proposal.new_topology)
traj = md.Trajectory(np.array(htfs_t[1].old_positions(htfs_t[1].hybrid_positions)), top_old)
traj.save("2_complex_old.pdb")
traj = md.Trajectory(np.array(htfs_t[1].new_positions(htfs_t[1].hybrid_positions)), top_new)
traj.save("2_complex_new.pdb")

## W44F

In [1]:
# Set up logger
import logging
_logger = logging.getLogger()
_logger.setLevel(logging.INFO)

In [2]:
# Solvent
from perses.app.relative_point_mutation_setup import PointMutationExecutor
from simtk import unit
solvent_delivery = PointMutationExecutor("../input/mmc2_barstar.pdb", 
                        '1', # First chain is the barstar one
                        '44', 
                        'PHE',
                        ligand_file="../input/mmc2_barnase.pdb",
                        ionic_strength=0.05*unit.molar
                       )




INFO:numexpr.utils:Note: detected 72 virtual cores but NumExpr set to maximum of 64, check "NUMEXPR_MAX_THREADS" environment variable.
INFO:numexpr.utils:Note: NumExpr detected 72 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
INFO:numexpr.utils:NumExpr defaulting to 8 threads.
RDKit WARNING: [10:42:27] Enabling RDKit 2019.09.3 jupyter extensions
INFO:root:solvating at 0.05 M using tip3p
INFO:root:solvating at 0.05 M using tip3p
INFO:proposal_generator:	Conducting polymer point mutation proposal...
INFO:proposal_generator:Using matching_criterion to chose best atom map
INFO:proposal_generator:Scaffold has symmetry of 0
INFO:proposal_generator:len [{4: 4, 5: 5, 7: 6, 6: 7, 8: 9, 9: 10, 10: 12, 13: 16, 14: 17, 16: 18, 18: 19, 17: 20, 19: 22}, {4: 4, 5: 5, 6: 6, 7: 7, 9: 9, 8: 10, 10: 12, 13: 16, 14: 17, 15: 18, 17: 19, 18: 20, 19: 22}, {4: 4, 5: 5, 7: 6, 6: 7, 8: 9, 10: 12, 9: 13, 14: 16, 13: 17, 16: 18, 17: 20, 19: 22, 18: 23}, {4: 4, 5: 5, 6: 6, 7: 7, 9: 9, 10: 

conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA


INFO:geometry:setting atoms_with_positions context new positions


conducting subsequent work with the following platform: CUDA


INFO:geometry:There are 14 new atoms
INFO:geometry:	reduced angle potential = 0.8029665450835769.
INFO:geometry:	reduced angle potential = 0.4416395837926518.
INFO:geometry:	reduced angle potential = 0.3554891981623474.
INFO:geometry:	reduced angle potential = 0.34624259367848587.
INFO:geometry:	reduced angle potential = 0.6348592323510591.
INFO:geometry:	reduced angle potential = 0.043021469624043955.
INFO:geometry:	reduced angle potential = 0.17697258595933663.
INFO:geometry:	reduced angle potential = 1.8246279497287425.
INFO:geometry:	reduced angle potential = 0.28110528117580674.
INFO:geometry:	reduced angle potential = 0.9197769487016747.
INFO:geometry:	reduced angle potential = 0.021407014433055167.
INFO:geometry:	reduced angle potential = 0.327806566401401.
INFO:geometry:	reduced angle potential = 1.8342630782014502.
INFO:geometry:	reduced angle potential = 0.2530801737457376.
INFO:geometry:	beginning construction of no_nonbonded final system...
INFO:geometry:	initial no-nonbond

...

conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA


INFO:geometry:total reduced energy added from growth system: 37.59649937183556
INFO:geometry:final reduced energy 4849.6240709408485
INFO:geometry:sum of energies: 4837.242021007394
INFO:geometry:magnitude of difference in the energies: 12.382049933453999
INFO:geometry:Final logp_proposal: 142.49421541629576


added energy components: [('CustomBondForce', 0.47685375494925697), ('CustomAngleForce', 1.7775022243071807), ('CustomTorsionForce', 8.891492452177019), ('CustomBondForce', 26.450650940402113)]


INFO:relative:Beginning nonbonded method, total particle, barostat, and exceptions retrieval...
INFO:relative:Old system forces: dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce', 'MonteCarloBarostat'])
INFO:relative:New system forces: dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce', 'MonteCarloBarostat'])
INFO:relative:No unknown forces.
INFO:relative:Nonbonded method to be used (i.e. from old system): 4
INFO:relative:Adding and mapping old atoms to hybrid system...
INFO:relative:Adding and mapping new atoms to hybrid system...
INFO:relative:Added MonteCarloBarostat.
INFO:relative:getDefaultPeriodicBoxVectors added to hybrid: [Quantity(value=Vec3(x=6.7997, y=0.0, z=0.0), unit=nanometer), Quantity(value=Vec3(x=0.0, y=6.7997, z=0.0), unit=nanometer), Quantity(value=Vec3(x=0.0, y=0.0, z=6.7997), unit=nanometer)]
INFO:relative:Determined atom classes.
INFO:relative:Generating old system exceptions 

conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA
			HarmonicBondForce: 189.69655643562666
			HarmonicAngleForce: 791.7773839676565
			PeriodicTorsionForce: 3830.521840699088
			NonbondedForce: -25533.061979926606
			AndersenThermostat: 0.0
			MonteCarloBarostat: 0.0
conducting subsequent work with the following platform: CUDA
			CustomBondForce: 1.5886270391663544
			HarmonicBondForce: 239.16971275540104
			CustomAngleForce: 6.623113005764122
			HarmonicAngleForce: 1119.060717591232
			CustomTorsionForce: 0.04958068808918507
			PeriodicTorsionForce: 3852.8231673456703
			NonbondedForce: -25327.221293930303
			CustomNonbondedForce: -91.81132286818999
			CustomBondForce: 0.0
			AndersenThermostat: 0.0
			MonteCarloBarostat: 0.0
conducting subsequent work with the following platform: CUDA
			CustomBondForce: 1.5886270391663544
			HarmonicBondForce: 239.16971275540104
			CustomAngleForce: 6.623113005764122
			Harmonic

In [3]:
solvent_delivery.get_complex_htf()

In [5]:
import pickle
import os
out_dir = '/data/chodera/zhangi/perses_benchmark/neq/6/'
pickle.dump(solvent_delivery.get_apo_htf(), open(os.path.join(out_dir, "3/3_apo.pickle"), "wb" ))
pickle.dump(solvent_delivery.get_complex_htf(), open(os.path.join(out_dir, "3/3_complex.pickle"), "wb" ))


In [4]:
import mdtraj as md
import numpy as np
htfs_t = [solvent_delivery.get_apo_htf(), solvent_delivery.get_complex_htf()]

top_old = md.Topology.from_openmm(htfs_t[0]._topology_proposal.old_topology)
top_new = md.Topology.from_openmm(htfs_t[0]._topology_proposal.new_topology)
traj = md.Trajectory(np.array(htfs_t[0].old_positions(htfs_t[0].hybrid_positions)), top_old)
traj.save("3_apo_old.pdb")
traj = md.Trajectory(np.array(htfs_t[0].new_positions(htfs_t[0].hybrid_positions)), top_new)
traj.save("3_apo_new.pdb")

top_old = md.Topology.from_openmm(htfs_t[1]._topology_proposal.old_topology)
top_new = md.Topology.from_openmm(htfs_t[1]._topology_proposal.new_topology)
traj = md.Trajectory(np.array(htfs_t[1].old_positions(htfs_t[1].hybrid_positions)), top_old)
traj.save("3_complex_old.pdb")
traj = md.Trajectory(np.array(htfs_t[1].new_positions(htfs_t[1].hybrid_positions)), top_new)
traj.save("3_complex_new.pdb")

In [2]:
import pickle 
import os
out_dir = '/data/chodera/zhangi/perses_benchmark/neq/6/'
with open(os.path.join(out_dir, "3/3_apo.pickle"), "rb" ) as f:
    htf = pickle.load(f)

In [6]:
for bond in solvent_delivery.get_apo_htf()._topology_proposal.new_topology.bonds():
    if bond[0].residue.name == 'PHE' or bond[1].residue.name == 'PHE':
        print(bond)

Bond(<Atom 685 (C) of chain 0 residue 43 (GLY)>, <Atom 690 (N) of chain 0 residue 44 (PHE)>)
Bond(<Atom 691 (CA) of chain 0 residue 44 (PHE)>, <Atom 692 (C) of chain 0 residue 44 (PHE)>)
Bond(<Atom 692 (C) of chain 0 residue 44 (PHE)>, <Atom 693 (O) of chain 0 residue 44 (PHE)>)
Bond(<Atom 691 (CA) of chain 0 residue 44 (PHE)>, <Atom 694 (CB) of chain 0 residue 44 (PHE)>)
Bond(<Atom 691 (CA) of chain 0 residue 44 (PHE)>, <Atom 700 (HA) of chain 0 residue 44 (PHE)>)
Bond(<Atom 690 (N) of chain 0 residue 44 (PHE)>, <Atom 691 (CA) of chain 0 residue 44 (PHE)>)
Bond(<Atom 694 (CB) of chain 0 residue 44 (PHE)>, <Atom 695 (CG) of chain 0 residue 44 (PHE)>)
Bond(<Atom 694 (CB) of chain 0 residue 44 (PHE)>, <Atom 702 (HB2) of chain 0 residue 44 (PHE)>)
Bond(<Atom 694 (CB) of chain 0 residue 44 (PHE)>, <Atom 701 (HB3) of chain 0 residue 44 (PHE)>)
Bond(<Atom 695 (CG) of chain 0 residue 44 (PHE)>, <Atom 696 (CD1) of chain 0 residue 44 (PHE)>)
Bond(<Atom 696 (CD1) of chain 0 residue 44 (PHE)>, <A

## Y29F

In [1]:
# Set up logger
import logging
_logger = logging.getLogger()
_logger.setLevel(logging.INFO)

In [2]:
# Solvent
from perses.app.relative_point_mutation_setup import PointMutationExecutor
from simtk import unit
solvent_delivery = PointMutationExecutor("../input/mmc2_barstar.pdb", 
                        '1', # First chain is the barstar one
                        '29', 
                        'PHE',
                        ligand_file="../input/mmc2_barnase.pdb",
                        ionic_strength=0.05*unit.molar
                       )




INFO:numexpr.utils:Note: detected 72 virtual cores but NumExpr set to maximum of 64, check "NUMEXPR_MAX_THREADS" environment variable.
INFO:numexpr.utils:Note: NumExpr detected 72 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
INFO:numexpr.utils:NumExpr defaulting to 8 threads.
DEBUG:numba.core.byteflow:bytecode dump:
>          0	NOP(arg=None, lineno=6)
           2	LOAD_GLOBAL(arg=0, lineno=6)
           4	LOAD_METHOD(arg=1, lineno=6)
           6	LOAD_CONST(arg=1, lineno=6)
           8	CALL_METHOD(arg=1, lineno=6)
          10	STORE_FAST(arg=2, lineno=6)
          12	LOAD_FAST(arg=0, lineno=7)
          14	LOAD_CONST(arg=2, lineno=7)
          16	BINARY_SUBSCR(arg=None, lineno=7)
          18	LOAD_FAST(arg=1, lineno=7)
          20	LOAD_CONST(arg=3, lineno=7)
          22	BINARY_SUBSCR(arg=None, lineno=7)
          24	BINARY_MULTIPLY(arg=None, lineno=7)
          26	LOAD_FAST(arg=0, lineno=7)
          28	LOAD_CONST(arg=3, lineno=7)
          30	BINARY_SUBSC

DEBUG:numba.core.byteflow:stack ['$60binary_multiply.27', '$66binary_subscr.30', '$b68.31']
DEBUG:numba.core.byteflow:dispatch pc=72, inst=BINARY_SUBSCR(arg=None, lineno=8)
DEBUG:numba.core.byteflow:stack ['$60binary_multiply.27', '$66binary_subscr.30', '$b68.31', '$const70.32']
DEBUG:numba.core.byteflow:dispatch pc=74, inst=BINARY_MULTIPLY(arg=None, lineno=8)
DEBUG:numba.core.byteflow:stack ['$60binary_multiply.27', '$66binary_subscr.30', '$72binary_subscr.33']
DEBUG:numba.core.byteflow:dispatch pc=76, inst=BINARY_SUBTRACT(arg=None, lineno=8)
DEBUG:numba.core.byteflow:stack ['$60binary_multiply.27', '$74binary_multiply.34']
DEBUG:numba.core.byteflow:dispatch pc=78, inst=LOAD_FAST(arg=2, lineno=8)
DEBUG:numba.core.byteflow:stack ['$76binary_subtract.35']
DEBUG:numba.core.byteflow:dispatch pc=80, inst=LOAD_CONST(arg=2, lineno=8)
DEBUG:numba.core.byteflow:stack ['$76binary_subtract.35', '$c78.36']
DEBUG:numba.core.byteflow:dispatch pc=82, inst=STORE_SUBSCR(arg=None, lineno=8)
DEBUG:numba

DEBUG:numba.core.interpreter:label 0:
    a = arg(0, name=a)                       ['a']
    b = arg(1, name=b)                       ['b']
    $2load_global.0 = global(np: <module 'numpy' from '/home/zhangi/miniconda3/envs/perses-sims/lib/python3.7/site-packages/numpy/__init__.py'>) ['$2load_global.0']
    $4load_method.1 = getattr(value=$2load_global.0, attr=zeros) ['$2load_global.0', '$4load_method.1']
    $const6.2 = const(int, 3)                ['$const6.2']
    $8call_method.3 = call $4load_method.1($const6.2, func=$4load_method.1, args=[Var($const6.2, coordinate_numba.py:6)], kws=(), vararg=None) ['$4load_method.1', '$8call_method.3', '$const6.2']
    c = $8call_method.3                      ['$8call_method.3', 'c']
    $const14.5 = const(int, 1)               ['$const14.5']
    $16binary_subscr.6 = getitem(value=a, index=$const14.5) ['$16binary_subscr.6', '$const14.5', 'a']
    $const20.8 = const(int, 2)               ['$const20.8']
    $22binary_subscr.9 = getitem(value=b, ind

DEBUG:numba.core.ssa:================================================================================
DEBUG:numba.core.ssa:==== SSA block analysis pass on 0
DEBUG:numba.core.ssa:Running <numba.core.ssa._GatherDefsHandler object at 0x2b9fc8d9f908>
DEBUG:numba.core.ssa:on stmt: a = arg(0, name=a)
DEBUG:numba.core.ssa:on stmt: b = arg(1, name=b)
DEBUG:numba.core.ssa:on stmt: $2load_global.0 = global(np: <module 'numpy' from '/home/zhangi/miniconda3/envs/perses-sims/lib/python3.7/site-packages/numpy/__init__.py'>)
DEBUG:numba.core.ssa:on stmt: $4load_method.1 = getattr(value=$2load_global.0, attr=zeros)
DEBUG:numba.core.ssa:on stmt: $const6.2 = const(int, 3)
DEBUG:numba.core.ssa:on stmt: $8call_method.3 = call $4load_method.1($const6.2, func=$4load_method.1, args=[Var($const6.2, coordinate_numba.py:6)], kws=(), vararg=None)
DEBUG:numba.core.ssa:on stmt: c = $8call_method.3
DEBUG:numba.core.ssa:on stmt: $const14.5 = const(int, 1)
DEBUG:numba.core.ssa:on stmt: $16binary_subscr.6 = static_get

DEBUG:numba.core.ssa:================================================================================


KeyboardInterrupt: 

In [3]:
import pickle
import os
out_dir = '/data/chodera/zhangi/perses_benchmark/neq/6/'
pickle.dump(solvent_delivery.get_apo_htf(), open(os.path.join(out_dir, "4/4_apo.pickle"), "wb" ))
pickle.dump(solvent_delivery.get_complex_htf(), open(os.path.join(out_dir, "4/4_complex.pickle"), "wb" ))


In [4]:
import mdtraj as md
import numpy as np
htfs_t = [solvent_delivery.get_apo_htf(), solvent_delivery.get_complex_htf()]

top_old = md.Topology.from_openmm(htfs_t[0]._topology_proposal.old_topology)
top_new = md.Topology.from_openmm(htfs_t[0]._topology_proposal.new_topology)
traj = md.Trajectory(np.array(htfs_t[0].old_positions(htfs_t[0].hybrid_positions)), top_old)
traj.save("4_apo_old.pdb")
traj = md.Trajectory(np.array(htfs_t[0].new_positions(htfs_t[0].hybrid_positions)), top_new)
traj.save("4_apo_new.pdb")

top_old = md.Topology.from_openmm(htfs_t[1]._topology_proposal.old_topology)
top_new = md.Topology.from_openmm(htfs_t[1]._topology_proposal.new_topology)
traj = md.Trajectory(np.array(htfs_t[1].old_positions(htfs_t[1].hybrid_positions)), top_old)
traj.save("4_complex_old.pdb")
traj = md.Trajectory(np.array(htfs_t[1].new_positions(htfs_t[1].hybrid_positions)), top_new)
traj.save("4_complex_new.pdb")

# Renumber NME residue in fah pdbs

In [8]:
from simtk.openmm import app
pdb = app.PDBFile("/data/chodera/zhangi/perses_benchmark/fah/mmc2_barnase.pdb")

In [71]:
for res in pdb.topology.residues():
    if res.name == 'NME':
        res.id = '111'
        res.insertionCode = ''

In [23]:
for res in pdb.topology.residues():
    print(res, res.id)

<Residue 0 (ACE) of chain 0> 2
<Residue 1 (VAL) of chain 0> 3
<Residue 2 (ILE) of chain 0> 4
<Residue 3 (ASN) of chain 0> 5
<Residue 4 (THR) of chain 0> 6
<Residue 5 (PHE) of chain 0> 7
<Residue 6 (ASP) of chain 0> 8
<Residue 7 (GLY) of chain 0> 9
<Residue 8 (VAL) of chain 0> 10
<Residue 9 (ALA) of chain 0> 11
<Residue 10 (ASP) of chain 0> 12
<Residue 11 (TYR) of chain 0> 13
<Residue 12 (LEU) of chain 0> 14
<Residue 13 (GLN) of chain 0> 15
<Residue 14 (THR) of chain 0> 16
<Residue 15 (TYR) of chain 0> 17
<Residue 16 (HIS) of chain 0> 18
<Residue 17 (LYS) of chain 0> 19
<Residue 18 (LEU) of chain 0> 20
<Residue 19 (PRO) of chain 0> 21
<Residue 20 (ASP) of chain 0> 22
<Residue 21 (ASN) of chain 0> 23
<Residue 22 (TYR) of chain 0> 24
<Residue 23 (ILE) of chain 0> 25
<Residue 24 (THR) of chain 0> 26
<Residue 25 (LYS) of chain 0> 27
<Residue 26 (SER) of chain 0> 28
<Residue 27 (GLU) of chain 0> 29
<Residue 28 (ALA) of chain 0> 30
<Residue 29 (GLN) of chain 0> 31
<Residue 30 (ALA) of chain 0

In [72]:
app.PDBFile.writeFile(pdb.topology, pdb.positions, open("/data/chodera/zhangi/perses_benchmark/fah/mmc2_barnase.pdb", 'w'), keepIds=True)


In [67]:
pdb = app.PDBFile("/data/chodera/zhangi/perses_benchmark/fah/mmc2_barstar.pdb")

In [68]:
for res in pdb.topology.residues():
    if res.name == 'NME':
        res.id = '90'
        res.insertionCode = ''

In [69]:
app.PDBFile.writeFile(pdb.topology, pdb.positions, open("/data/chodera/zhangi/perses_benchmark/fah/mmc2_barstar.pdb", 'w'), keepIds=True)


In [96]:
pdb = app.PDBFile("/data/chodera/zhangi/perses_benchmark/fah/mmc2_barstar_T42A.pdb")

In [97]:
for res in pdb.topology.residues():
    if res.name == 'NME':
        res.id = '90'
        res.insertionCode = ''

In [98]:
modeller = app.Modeller(pdb.topology, pdb.positions)
chains = list(pdb.topology.chains())
modeller.delete([chains[2], chains[3]])


In [99]:
app.PDBFile.writeFile(modeller.topology, modeller.positions, open("/data/chodera/zhangi/perses_benchmark/fah/mmc2_barstar_T42A.pdb", 'w'), keepIds=True)


In [103]:
pdb = app.PDBFile("/data/chodera/zhangi/perses_benchmark/fah/mmc2_barstar_Y29A.pdb")

In [104]:
for res in pdb.topology.residues():
    if res.name == 'NME':
        res.id = '90'
        res.insertionCode = ''

In [105]:
modeller = app.Modeller(pdb.topology, pdb.positions)
chains = list(pdb.topology.chains())
modeller.delete([chains[2], chains[3]])


In [106]:
app.PDBFile.writeFile(modeller.topology, modeller.positions, open("/data/chodera/zhangi/perses_benchmark/fah/mmc2_barstar_Y29A.pdb", 'w'), keepIds=True)


In [107]:
pdb = app.PDBFile("/data/chodera/zhangi/perses_benchmark/fah/mmc2_barstar_W38F.pdb")

In [108]:
for res in pdb.topology.residues():
    if res.name == 'NME':
        res.id = '90'
        res.insertionCode = ''

In [109]:
modeller = app.Modeller(pdb.topology, pdb.positions)
chains = list(pdb.topology.chains())
modeller.delete([chains[2], chains[3]])


In [110]:
app.PDBFile.writeFile(modeller.topology, modeller.positions, open("/data/chodera/zhangi/perses_benchmark/fah/mmc2_barstar_W38F.pdb", 'w'), keepIds=True)


In [9]:
pdb = app.PDBFile("/data/chodera/zhangi/perses_benchmark/fah/mmc2_barstar_W44F.pdb")

/home/zhangi/miniconda3/envs/perses-sims/lib/python3.7/site-packages/simtk/openmm/app/internal/pdbstructure.py:443: UserWarning: WARNING: two consecutive residues with same number (ATOM   1432  N   NME A  89      50.032  32.154  -8.609  1.00  0.00           N  , ATOM   1431  HG  SER A  89      51.018  34.037  -5.289  1.00  0.00           H  )
  warnings.warn("WARNING: two consecutive residues with same number (%s, %s)" % (atom, self._current_residue.atoms[-1]))


In [10]:
for res in pdb.topology.residues():
    if res.name == 'NME':
        res.id = '90'
        res.insertionCode = ''

In [11]:
modeller = app.Modeller(pdb.topology, pdb.positions)
chains = list(pdb.topology.chains())
modeller.delete([chains[2], chains[3]])


In [12]:
app.PDBFile.writeFile(modeller.topology, modeller.positions, open("/data/chodera/zhangi/perses_benchmark/fah/mmc2_barstar_W44F.pdb", 'w'), keepIds=True)


In [115]:
pdb = app.PDBFile("/data/chodera/zhangi/perses_benchmark/fah/mmc2_barstar_Y29F.pdb")

In [116]:
for res in pdb.topology.residues():
    if res.name == 'NME':
        res.id = '90'
        res.insertionCode = ''

In [117]:
modeller = app.Modeller(pdb.topology, pdb.positions)
chains = list(pdb.topology.chains())
modeller.delete([chains[2], chains[3]])


In [118]:
app.PDBFile.writeFile(modeller.topology, modeller.positions, open("/data/chodera/zhangi/perses_benchmark/fah/mmc2_barstar_Y29F.pdb", 'w'), keepIds=True)


# A42T (for 2 fs -- no HBond constraints)

In [4]:
# Check whether existing apo and complex htfs have no HBond constraints
import os
import pickle
with open(os.path.join("/data/chodera/zhangi/perses_benchmark/neq/8/3", f"3_complex.pickle"), 'rb') as f:
    complex_htf = pickle.load(f)

In [6]:
for i in range(complex_htf.hybrid_system.getNumConstraints()):
    print(complex_htf.hybrid_system.getConstraintParameters(i))

[1437, 1438, Quantity(value=0.09572, unit=nanometer)]
[1437, 1439, Quantity(value=0.09572, unit=nanometer)]
[3149, 3150, Quantity(value=0.09572, unit=nanometer)]
[3149, 3151, Quantity(value=0.09572, unit=nanometer)]
[3152, 3153, Quantity(value=0.09572, unit=nanometer)]
[3152, 3154, Quantity(value=0.09572, unit=nanometer)]
[3155, 3156, Quantity(value=0.09572, unit=nanometer)]
[3155, 3157, Quantity(value=0.09572, unit=nanometer)]
[3158, 3159, Quantity(value=0.09572, unit=nanometer)]
[3158, 3160, Quantity(value=0.09572, unit=nanometer)]
[3161, 3162, Quantity(value=0.09572, unit=nanometer)]
[3161, 3163, Quantity(value=0.09572, unit=nanometer)]
[3164, 3165, Quantity(value=0.09572, unit=nanometer)]
[3164, 3166, Quantity(value=0.09572, unit=nanometer)]
[3167, 3168, Quantity(value=0.09572, unit=nanometer)]
[3167, 3169, Quantity(value=0.09572, unit=nanometer)]
[3170, 3171, Quantity(value=0.09572, unit=nanometer)]
[3170, 3172, Quantity(value=0.09572, unit=nanometer)]
[3173, 3174, Quantity(value=

[3536, 3538, Quantity(value=0.09572, unit=nanometer)]
[3539, 3540, Quantity(value=0.09572, unit=nanometer)]
[3539, 3541, Quantity(value=0.09572, unit=nanometer)]
[3542, 3543, Quantity(value=0.09572, unit=nanometer)]
[3542, 3544, Quantity(value=0.09572, unit=nanometer)]
[3545, 3546, Quantity(value=0.09572, unit=nanometer)]
[3545, 3547, Quantity(value=0.09572, unit=nanometer)]
[3548, 3549, Quantity(value=0.09572, unit=nanometer)]
[3548, 3550, Quantity(value=0.09572, unit=nanometer)]
[3551, 3552, Quantity(value=0.09572, unit=nanometer)]
[3551, 3553, Quantity(value=0.09572, unit=nanometer)]
[3554, 3555, Quantity(value=0.09572, unit=nanometer)]
[3554, 3556, Quantity(value=0.09572, unit=nanometer)]
[3557, 3558, Quantity(value=0.09572, unit=nanometer)]
[3557, 3559, Quantity(value=0.09572, unit=nanometer)]
[3560, 3561, Quantity(value=0.09572, unit=nanometer)]
[3560, 3562, Quantity(value=0.09572, unit=nanometer)]
[3563, 3564, Quantity(value=0.09572, unit=nanometer)]
[3563, 3565, Quantity(value=

[8321, 8322, Quantity(value=0.09572, unit=nanometer)]
[8321, 8323, Quantity(value=0.09572, unit=nanometer)]
[8324, 8325, Quantity(value=0.09572, unit=nanometer)]
[8324, 8326, Quantity(value=0.09572, unit=nanometer)]
[8327, 8328, Quantity(value=0.09572, unit=nanometer)]
[8327, 8329, Quantity(value=0.09572, unit=nanometer)]
[8330, 8331, Quantity(value=0.09572, unit=nanometer)]
[8330, 8332, Quantity(value=0.09572, unit=nanometer)]
[8333, 8334, Quantity(value=0.09572, unit=nanometer)]
[8333, 8335, Quantity(value=0.09572, unit=nanometer)]
[8336, 8337, Quantity(value=0.09572, unit=nanometer)]
[8336, 8338, Quantity(value=0.09572, unit=nanometer)]
[8339, 8340, Quantity(value=0.09572, unit=nanometer)]
[8339, 8341, Quantity(value=0.09572, unit=nanometer)]
[8342, 8343, Quantity(value=0.09572, unit=nanometer)]
[8342, 8344, Quantity(value=0.09572, unit=nanometer)]
[8345, 8346, Quantity(value=0.09572, unit=nanometer)]
[8345, 8347, Quantity(value=0.09572, unit=nanometer)]
[8348, 8349, Quantity(value=

[12818, 12820, Quantity(value=0.09572, unit=nanometer)]
[12821, 12822, Quantity(value=0.09572, unit=nanometer)]
[12821, 12823, Quantity(value=0.09572, unit=nanometer)]
[12824, 12825, Quantity(value=0.09572, unit=nanometer)]
[12824, 12826, Quantity(value=0.09572, unit=nanometer)]
[12827, 12828, Quantity(value=0.09572, unit=nanometer)]
[12827, 12829, Quantity(value=0.09572, unit=nanometer)]
[12830, 12831, Quantity(value=0.09572, unit=nanometer)]
[12830, 12832, Quantity(value=0.09572, unit=nanometer)]
[12833, 12834, Quantity(value=0.09572, unit=nanometer)]
[12833, 12835, Quantity(value=0.09572, unit=nanometer)]
[12836, 12837, Quantity(value=0.09572, unit=nanometer)]
[12836, 12838, Quantity(value=0.09572, unit=nanometer)]
[12839, 12840, Quantity(value=0.09572, unit=nanometer)]
[12839, 12841, Quantity(value=0.09572, unit=nanometer)]
[12842, 12843, Quantity(value=0.09572, unit=nanometer)]
[12842, 12844, Quantity(value=0.09572, unit=nanometer)]
[12845, 12846, Quantity(value=0.09572, unit=nano

[17318, 17320, Quantity(value=0.09572, unit=nanometer)]
[17321, 17322, Quantity(value=0.09572, unit=nanometer)]
[17321, 17323, Quantity(value=0.09572, unit=nanometer)]
[17324, 17325, Quantity(value=0.09572, unit=nanometer)]
[17324, 17326, Quantity(value=0.09572, unit=nanometer)]
[17327, 17328, Quantity(value=0.09572, unit=nanometer)]
[17327, 17329, Quantity(value=0.09572, unit=nanometer)]
[17330, 17331, Quantity(value=0.09572, unit=nanometer)]
[17330, 17332, Quantity(value=0.09572, unit=nanometer)]
[17333, 17334, Quantity(value=0.09572, unit=nanometer)]
[17333, 17335, Quantity(value=0.09572, unit=nanometer)]
[17336, 17337, Quantity(value=0.09572, unit=nanometer)]
[17336, 17338, Quantity(value=0.09572, unit=nanometer)]
[17339, 17340, Quantity(value=0.09572, unit=nanometer)]
[17339, 17341, Quantity(value=0.09572, unit=nanometer)]
[17342, 17343, Quantity(value=0.09572, unit=nanometer)]
[17342, 17344, Quantity(value=0.09572, unit=nanometer)]
[17345, 17346, Quantity(value=0.09572, unit=nano

[22568, 22569, Quantity(value=0.09572, unit=nanometer)]
[22568, 22570, Quantity(value=0.09572, unit=nanometer)]
[22571, 22572, Quantity(value=0.09572, unit=nanometer)]
[22571, 22573, Quantity(value=0.09572, unit=nanometer)]
[22574, 22575, Quantity(value=0.09572, unit=nanometer)]
[22574, 22576, Quantity(value=0.09572, unit=nanometer)]
[22577, 22578, Quantity(value=0.09572, unit=nanometer)]
[22577, 22579, Quantity(value=0.09572, unit=nanometer)]
[22580, 22581, Quantity(value=0.09572, unit=nanometer)]
[22580, 22582, Quantity(value=0.09572, unit=nanometer)]
[22583, 22584, Quantity(value=0.09572, unit=nanometer)]
[22583, 22585, Quantity(value=0.09572, unit=nanometer)]
[22586, 22587, Quantity(value=0.09572, unit=nanometer)]
[22586, 22588, Quantity(value=0.09572, unit=nanometer)]
[22589, 22590, Quantity(value=0.09572, unit=nanometer)]
[22589, 22591, Quantity(value=0.09572, unit=nanometer)]
[22592, 22593, Quantity(value=0.09572, unit=nanometer)]
[22592, 22594, Quantity(value=0.09572, unit=nano

[27818, 27819, Quantity(value=0.09572, unit=nanometer)]
[27818, 27820, Quantity(value=0.09572, unit=nanometer)]
[27821, 27822, Quantity(value=0.09572, unit=nanometer)]
[27821, 27823, Quantity(value=0.09572, unit=nanometer)]
[27824, 27825, Quantity(value=0.09572, unit=nanometer)]
[27824, 27826, Quantity(value=0.09572, unit=nanometer)]
[27827, 27828, Quantity(value=0.09572, unit=nanometer)]
[27827, 27829, Quantity(value=0.09572, unit=nanometer)]
[27830, 27831, Quantity(value=0.09572, unit=nanometer)]
[27830, 27832, Quantity(value=0.09572, unit=nanometer)]
[27833, 27834, Quantity(value=0.09572, unit=nanometer)]
[27833, 27835, Quantity(value=0.09572, unit=nanometer)]
[27836, 27837, Quantity(value=0.09572, unit=nanometer)]
[27836, 27838, Quantity(value=0.09572, unit=nanometer)]
[27839, 27840, Quantity(value=0.09572, unit=nanometer)]
[27839, 27841, Quantity(value=0.09572, unit=nanometer)]
[27842, 27843, Quantity(value=0.09572, unit=nanometer)]
[27842, 27844, Quantity(value=0.09572, unit=nano

[10572, 10573, Quantity(value=0.15139006545247014, unit=nanometer)]
[10575, 10576, Quantity(value=0.15139006545247014, unit=nanometer)]
[10578, 10579, Quantity(value=0.15139006545247014, unit=nanometer)]
[10581, 10582, Quantity(value=0.15139006545247014, unit=nanometer)]
[10584, 10585, Quantity(value=0.15139006545247014, unit=nanometer)]
[10587, 10588, Quantity(value=0.15139006545247014, unit=nanometer)]
[10590, 10591, Quantity(value=0.15139006545247014, unit=nanometer)]
[10593, 10594, Quantity(value=0.15139006545247014, unit=nanometer)]
[10596, 10597, Quantity(value=0.15139006545247014, unit=nanometer)]
[10599, 10600, Quantity(value=0.15139006545247014, unit=nanometer)]
[10602, 10603, Quantity(value=0.15139006545247014, unit=nanometer)]
[10605, 10606, Quantity(value=0.15139006545247014, unit=nanometer)]
[10608, 10609, Quantity(value=0.15139006545247014, unit=nanometer)]
[10611, 10612, Quantity(value=0.15139006545247014, unit=nanometer)]
[10614, 10615, Quantity(value=0.1513900654524701

[21072, 21073, Quantity(value=0.15139006545247014, unit=nanometer)]
[21075, 21076, Quantity(value=0.15139006545247014, unit=nanometer)]
[21078, 21079, Quantity(value=0.15139006545247014, unit=nanometer)]
[21081, 21082, Quantity(value=0.15139006545247014, unit=nanometer)]
[21084, 21085, Quantity(value=0.15139006545247014, unit=nanometer)]
[21087, 21088, Quantity(value=0.15139006545247014, unit=nanometer)]
[21090, 21091, Quantity(value=0.15139006545247014, unit=nanometer)]
[21093, 21094, Quantity(value=0.15139006545247014, unit=nanometer)]
[21096, 21097, Quantity(value=0.15139006545247014, unit=nanometer)]
[21099, 21100, Quantity(value=0.15139006545247014, unit=nanometer)]
[21102, 21103, Quantity(value=0.15139006545247014, unit=nanometer)]
[21105, 21106, Quantity(value=0.15139006545247014, unit=nanometer)]
[21108, 21109, Quantity(value=0.15139006545247014, unit=nanometer)]
[21111, 21112, Quantity(value=0.15139006545247014, unit=nanometer)]
[21114, 21115, Quantity(value=0.1513900654524701

In [7]:
for atom in complex_htf.hybrid_topology.atoms:
    print(atom, atom.index)

ACE0-CH3 0
ACE0-C 1
ACE0-O 2
ACE0-H1 3
ACE0-H2 4
ACE0-H3 5
LYS1-N 6
LYS1-CA 7
LYS1-C 8
LYS1-O 9
LYS1-CB 10
LYS1-CG 11
LYS1-CD 12
LYS1-CE 13
LYS1-NZ 14
LYS1-H2 15
LYS1-HA 16
LYS1-HB3 17
LYS1-HB2 18
LYS1-HG2 19
LYS1-HG3 20
LYS1-HD2 21
LYS1-HD3 22
LYS1-HE3 23
LYS1-HE2 24
LYS1-HZ1 25
LYS1-HZ2 26
LYS1-HZ3 27
LYS2-N 28
LYS2-CA 29
LYS2-C 30
LYS2-O 31
LYS2-CB 32
LYS2-CG 33
LYS2-CD 34
LYS2-CE 35
LYS2-NZ 36
LYS2-H 37
LYS2-HA 38
LYS2-HB3 39
LYS2-HB2 40
LYS2-HG2 41
LYS2-HG3 42
LYS2-HD3 43
LYS2-HD2 44
LYS2-HE3 45
LYS2-HE2 46
LYS2-HZ1 47
LYS2-HZ2 48
LYS2-HZ3 49
ALA3-N 50
ALA3-CA 51
ALA3-C 52
ALA3-O 53
ALA3-CB 54
ALA3-H 55
ALA3-HA 56
ALA3-HB1 57
ALA3-HB2 58
ALA3-HB3 59
VAL4-N 60
VAL4-CA 61
VAL4-C 62
VAL4-O 63
VAL4-CB 64
VAL4-CG1 65
VAL4-CG2 66
VAL4-H 67
VAL4-HA 68
VAL4-HB 69
VAL4-HG11 70
VAL4-HG12 71
VAL4-HG13 72
VAL4-HG21 73
VAL4-HG22 74
VAL4-HG23 75
ILE5-N 76
ILE5-CA 77
ILE5-C 78
ILE5-O 79
ILE5-CB 80
ILE5-CG1 81
ILE5-CG2 82
ILE5-CD1 83
ILE5-H 84
ILE5-HA 85
ILE5-HB 86
ILE5-HG13 87
ILE5-HG12 88
ILE5-

SER28-HA 1859
SER28-HB2 1860
SER28-HB3 1861
SER28-HG 1862
GLU29-N 1863
GLU29-CA 1864
GLU29-C 1865
GLU29-O 1866
GLU29-CB 1867
GLU29-CG 1868
GLU29-CD 1869
GLU29-OE1 1870
GLU29-OE2 1871
GLU29-H 1872
GLU29-HA 1873
GLU29-HB3 1874
GLU29-HB2 1875
GLU29-HG3 1876
GLU29-HG2 1877
ALA30-N 1878
ALA30-CA 1879
ALA30-C 1880
ALA30-O 1881
ALA30-CB 1882
ALA30-H 1883
ALA30-HA 1884
ALA30-HB1 1885
ALA30-HB2 1886
ALA30-HB3 1887
GLN31-N 1888
GLN31-CA 1889
GLN31-C 1890
GLN31-O 1891
GLN31-CB 1892
GLN31-CG 1893
GLN31-CD 1894
GLN31-OE1 1895
GLN31-NE2 1896
GLN31-H 1897
GLN31-HA 1898
GLN31-HB2 1899
GLN31-HB3 1900
GLN31-HG3 1901
GLN31-HG2 1902
GLN31-HE21 1903
GLN31-HE22 1904
ALA32-N 1905
ALA32-CA 1906
ALA32-C 1907
ALA32-O 1908
ALA32-CB 1909
ALA32-H 1910
ALA32-HA 1911
ALA32-HB1 1912
ALA32-HB2 1913
ALA32-HB3 1914
LEU33-N 1915
LEU33-CA 1916
LEU33-C 1917
LEU33-O 1918
LEU33-CB 1919
LEU33-CG 1920
LEU33-CD1 1921
LEU33-CD2 1922
LEU33-H 1923
LEU33-HA 1924
LEU33-HB2 1925
LEU33-HB3 1926
LEU33-HG 1927
LEU33-HD11 1928
LEU33-HD12

HOH357-H1 3609
HOH357-H2 3610
HOH358-O 3611
HOH358-H1 3612
HOH358-H2 3613
HOH359-O 3614
HOH359-H1 3615
HOH359-H2 3616
HOH360-O 3617
HOH360-H1 3618
HOH360-H2 3619
HOH361-O 3620
HOH361-H1 3621
HOH361-H2 3622
HOH362-O 3623
HOH362-H1 3624
HOH362-H2 3625
HOH363-O 3626
HOH363-H1 3627
HOH363-H2 3628
HOH364-O 3629
HOH364-H1 3630
HOH364-H2 3631
HOH365-O 3632
HOH365-H1 3633
HOH365-H2 3634
HOH366-O 3635
HOH366-H1 3636
HOH366-H2 3637
HOH367-O 3638
HOH367-H1 3639
HOH367-H2 3640
HOH368-O 3641
HOH368-H1 3642
HOH368-H2 3643
HOH369-O 3644
HOH369-H1 3645
HOH369-H2 3646
HOH370-O 3647
HOH370-H1 3648
HOH370-H2 3649
HOH371-O 3650
HOH371-H1 3651
HOH371-H2 3652
HOH372-O 3653
HOH372-H1 3654
HOH372-H2 3655
HOH373-O 3656
HOH373-H1 3657
HOH373-H2 3658
HOH374-O 3659
HOH374-H1 3660
HOH374-H2 3661
HOH375-O 3662
HOH375-H1 3663
HOH375-H2 3664
HOH376-O 3665
HOH376-H1 3666
HOH376-H2 3667
HOH377-O 3668
HOH377-H1 3669
HOH377-H2 3670
HOH378-O 3671
HOH378-H1 3672
HOH378-H2 3673
HOH379-O 3674
HOH379-H1 3675
HOH379-H2 3676
HO

HOH943-H1 5358
HOH943-H2 5359
HOH944-O 5360
HOH944-H1 5361
HOH944-H2 5362
HOH945-O 5363
HOH945-H1 5364
HOH945-H2 5365
HOH946-O 5366
HOH946-H1 5367
HOH946-H2 5368
HOH947-O 5369
HOH947-H1 5370
HOH947-H2 5371
HOH948-O 5372
HOH948-H1 5373
HOH948-H2 5374
HOH949-O 5375
HOH949-H1 5376
HOH949-H2 5377
HOH950-O 5378
HOH950-H1 5379
HOH950-H2 5380
HOH951-O 5381
HOH951-H1 5382
HOH951-H2 5383
HOH952-O 5384
HOH952-H1 5385
HOH952-H2 5386
HOH953-O 5387
HOH953-H1 5388
HOH953-H2 5389
HOH954-O 5390
HOH954-H1 5391
HOH954-H2 5392
HOH955-O 5393
HOH955-H1 5394
HOH955-H2 5395
HOH956-O 5396
HOH956-H1 5397
HOH956-H2 5398
HOH957-O 5399
HOH957-H1 5400
HOH957-H2 5401
HOH958-O 5402
HOH958-H1 5403
HOH958-H2 5404
HOH959-O 5405
HOH959-H1 5406
HOH959-H2 5407
HOH960-O 5408
HOH960-H1 5409
HOH960-H2 5410
HOH961-O 5411
HOH961-H1 5412
HOH961-H2 5413
HOH962-O 5414
HOH962-H1 5415
HOH962-H2 5416
HOH963-O 5417
HOH963-H1 5418
HOH963-H2 5419
HOH964-O 5420
HOH964-H1 5421
HOH964-H2 5422
HOH965-O 5423
HOH965-H1 5424
HOH965-H2 5425
HO

HOH1526-H2 7108
HOH1527-O 7109
HOH1527-H1 7110
HOH1527-H2 7111
HOH1528-O 7112
HOH1528-H1 7113
HOH1528-H2 7114
HOH1529-O 7115
HOH1529-H1 7116
HOH1529-H2 7117
HOH1530-O 7118
HOH1530-H1 7119
HOH1530-H2 7120
HOH1531-O 7121
HOH1531-H1 7122
HOH1531-H2 7123
HOH1532-O 7124
HOH1532-H1 7125
HOH1532-H2 7126
HOH1533-O 7127
HOH1533-H1 7128
HOH1533-H2 7129
HOH1535-O 7130
HOH1535-H1 7131
HOH1535-H2 7132
HOH1536-O 7133
HOH1536-H1 7134
HOH1536-H2 7135
HOH1537-O 7136
HOH1537-H1 7137
HOH1537-H2 7138
HOH1538-O 7139
HOH1538-H1 7140
HOH1538-H2 7141
HOH1539-O 7142
HOH1539-H1 7143
HOH1539-H2 7144
HOH1540-O 7145
HOH1540-H1 7146
HOH1540-H2 7147
HOH1541-O 7148
HOH1541-H1 7149
HOH1541-H2 7150
HOH1542-O 7151
HOH1542-H1 7152
HOH1542-H2 7153
HOH1543-O 7154
HOH1543-H1 7155
HOH1543-H2 7156
HOH1544-O 7157
HOH1544-H1 7158
HOH1544-H2 7159
HOH1545-O 7160
HOH1545-H1 7161
HOH1545-H2 7162
HOH1546-O 7163
HOH1546-H1 7164
HOH1546-H2 7165
HOH1547-O 7166
HOH1547-H1 7167
HOH1547-H2 7168
HOH1548-O 7169
HOH1548-H1 7170
HOH1548-H2 71

...

HOH6223-H2 21106
HOH6224-O 21107
HOH6224-H1 21108
HOH6224-H2 21109
HOH6225-O 21110
HOH6225-H1 21111
HOH6225-H2 21112
HOH6226-O 21113
HOH6226-H1 21114
HOH6226-H2 21115
HOH6227-O 21116
HOH6227-H1 21117
HOH6227-H2 21118
HOH6228-O 21119
HOH6228-H1 21120
HOH6228-H2 21121
HOH6229-O 21122
HOH6229-H1 21123
HOH6229-H2 21124
HOH6230-O 21125
HOH6230-H1 21126
HOH6230-H2 21127
HOH6231-O 21128
HOH6231-H1 21129
HOH6231-H2 21130
HOH6232-O 21131
HOH6232-H1 21132
HOH6232-H2 21133
HOH6233-O 21134
HOH6233-H1 21135
HOH6233-H2 21136
HOH6234-O 21137
HOH6234-H1 21138
HOH6234-H2 21139
HOH6235-O 21140
HOH6235-H1 21141
HOH6235-H2 21142
HOH6236-O 21143
HOH6236-H1 21144
HOH6236-H2 21145
HOH6237-O 21146
HOH6237-H1 21147
HOH6237-H2 21148
HOH6238-O 21149
HOH6238-H1 21150
HOH6238-H2 21151
HOH6239-O 21152
HOH6239-H1 21153
HOH6239-H2 21154
HOH6240-O 21155
HOH6240-H1 21156
HOH6240-H2 21157
HOH6241-O 21158
HOH6241-H1 21159
HOH6241-H2 21160
HOH6242-O 21161
HOH6242-H1 21162
HOH6242-H2 21163
HOH6243-O 21164
HOH6243-H1 21165


HOH6810-O 22856
HOH6810-H1 22857
HOH6810-H2 22858
HOH6811-O 22859
HOH6811-H1 22860
HOH6811-H2 22861
HOH6812-O 22862
HOH6812-H1 22863
HOH6812-H2 22864
HOH6813-O 22865
HOH6813-H1 22866
HOH6813-H2 22867
HOH6814-O 22868
HOH6814-H1 22869
HOH6814-H2 22870
HOH6815-O 22871
HOH6815-H1 22872
HOH6815-H2 22873
HOH6816-O 22874
HOH6816-H1 22875
HOH6816-H2 22876
HOH6817-O 22877
HOH6817-H1 22878
HOH6817-H2 22879
HOH6818-O 22880
HOH6818-H1 22881
HOH6818-H2 22882
HOH6819-O 22883
HOH6819-H1 22884
HOH6819-H2 22885
HOH6820-O 22886
HOH6820-H1 22887
HOH6820-H2 22888
HOH6821-O 22889
HOH6821-H1 22890
HOH6821-H2 22891
HOH6822-O 22892
HOH6822-H1 22893
HOH6822-H2 22894
HOH6823-O 22895
HOH6823-H1 22896
HOH6823-H2 22897
HOH6824-O 22898
HOH6824-H1 22899
HOH6824-H2 22900
HOH6825-O 22901
HOH6825-H1 22902
HOH6825-H2 22903
HOH6826-O 22904
HOH6826-H1 22905
HOH6826-H2 22906
HOH6827-O 22907
HOH6827-H1 22908
HOH6827-H2 22909
HOH6828-O 22910
HOH6828-H1 22911
HOH6828-H2 22912
HOH6829-O 22913
HOH6829-H1 22914
HOH6829-H2 22915


HOH7396-H1 24606
HOH7396-H2 24607
HOH7397-O 24608
HOH7397-H1 24609
HOH7397-H2 24610
HOH7398-O 24611
HOH7398-H1 24612
HOH7398-H2 24613
HOH7399-O 24614
HOH7399-H1 24615
HOH7399-H2 24616
HOH7400-O 24617
HOH7400-H1 24618
HOH7400-H2 24619
HOH7401-O 24620
HOH7401-H1 24621
HOH7401-H2 24622
HOH7402-O 24623
HOH7402-H1 24624
HOH7402-H2 24625
HOH7403-O 24626
HOH7403-H1 24627
HOH7403-H2 24628
HOH7404-O 24629
HOH7404-H1 24630
HOH7404-H2 24631
HOH7405-O 24632
HOH7405-H1 24633
HOH7405-H2 24634
HOH7406-O 24635
HOH7406-H1 24636
HOH7406-H2 24637
HOH7407-O 24638
HOH7407-H1 24639
HOH7407-H2 24640
HOH7408-O 24641
HOH7408-H1 24642
HOH7408-H2 24643
HOH7409-O 24644
HOH7409-H1 24645
HOH7409-H2 24646
HOH7410-O 24647
HOH7410-H1 24648
HOH7410-H2 24649
HOH7411-O 24650
HOH7411-H1 24651
HOH7411-H2 24652
HOH7412-O 24653
HOH7412-H1 24654
HOH7412-H2 24655
HOH7413-O 24656
HOH7413-H1 24657
HOH7413-H2 24658
HOH7414-O 24659
HOH7414-H1 24660
HOH7414-H2 24661
HOH7415-O 24662
HOH7415-H1 24663
HOH7415-H2 24664
HOH7416-O 24665


HOH7981-H1 26355
HOH7981-H2 26356
HOH7982-O 26357
HOH7982-H1 26358
HOH7982-H2 26359
HOH7983-O 26360
HOH7983-H1 26361
HOH7983-H2 26362
HOH7984-O 26363
HOH7984-H1 26364
HOH7984-H2 26365
HOH7985-O 26366
HOH7985-H1 26367
HOH7985-H2 26368
HOH7986-O 26369
HOH7986-H1 26370
HOH7986-H2 26371
HOH7987-O 26372
HOH7987-H1 26373
HOH7987-H2 26374
HOH7988-O 26375
HOH7988-H1 26376
HOH7988-H2 26377
HOH7989-O 26378
HOH7989-H1 26379
HOH7989-H2 26380
HOH7990-O 26381
HOH7990-H1 26382
HOH7990-H2 26383
HOH7991-O 26384
HOH7991-H1 26385
HOH7991-H2 26386
HOH7992-O 26387
HOH7992-H1 26388
HOH7992-H2 26389
HOH7993-O 26390
HOH7993-H1 26391
HOH7993-H2 26392
HOH7994-O 26393
HOH7994-H1 26394
HOH7994-H2 26395
HOH7995-O 26396
HOH7995-H1 26397
HOH7995-H2 26398
HOH7996-O 26399
HOH7996-H1 26400
HOH7996-H2 26401
HOH7997-O 26402
HOH7997-H1 26403
HOH7997-H2 26404
HOH7998-O 26405
HOH7998-H1 26406
HOH7998-H2 26407
HOH7999-O 26408
HOH7999-H1 26409
HOH7999-H2 26410
HOH8000-O 26411
HOH8000-H1 26412
HOH8000-H2 26413
HOH8001-O 26414


HOH8569-H2 28105
HOH8570-O 28106
HOH8570-H1 28107
HOH8570-H2 28108
HOH8571-O 28109
HOH8571-H1 28110
HOH8571-H2 28111
HOH8572-O 28112
HOH8572-H1 28113
HOH8572-H2 28114
HOH8573-O 28115
HOH8573-H1 28116
HOH8573-H2 28117
HOH8574-O 28118
HOH8574-H1 28119
HOH8574-H2 28120
HOH8575-O 28121
HOH8575-H1 28122
HOH8575-H2 28123
HOH8576-O 28124
HOH8576-H1 28125
HOH8576-H2 28126
HOH8577-O 28127
HOH8577-H1 28128
HOH8577-H2 28129
HOH8578-O 28130
HOH8578-H1 28131
HOH8578-H2 28132
HOH8579-O 28133
HOH8579-H1 28134
HOH8579-H2 28135
HOH8580-O 28136
HOH8580-H1 28137
HOH8580-H2 28138
HOH8581-O 28139
HOH8581-H1 28140
HOH8581-H2 28141
HOH8582-O 28142
HOH8582-H1 28143
HOH8582-H2 28144
HOH8583-O 28145
HOH8583-H1 28146
HOH8583-H2 28147
HOH8584-O 28148
HOH8584-H1 28149
HOH8584-H2 28150
HOH8585-O 28151
HOH8585-H1 28152
HOH8585-H2 28153
HOH8586-O 28154
HOH8586-H1 28155
HOH8586-H2 28156
HOH8588-O 28157
HOH8588-H1 28158
HOH8588-H2 28159
HOH8589-O 28160
HOH8589-H1 28161
HOH8589-H2 28162
HOH8590-O 28163
HOH8590-H1 28164


In [10]:
complex_htf.hybrid_system.getParticleMass(1470)

Quantity(value=4.0, unit=dalton)

In [17]:
with open(os.path.join("/data/chodera/zhangi/perses_benchmark/neq/8/3", f"3_apo.pickle"), 'rb') as f:
    apo_htf = pickle.load(f)

In [18]:
for i in range(apo_htf.hybrid_system.getNumConstraints()):
    print(apo_htf.hybrid_system.getConstraintParameters(i))

[1437, 1438, Quantity(value=0.09572, unit=nanometer)]
[1437, 1439, Quantity(value=0.09572, unit=nanometer)]
[1440, 1441, Quantity(value=0.09572, unit=nanometer)]
[1440, 1442, Quantity(value=0.09572, unit=nanometer)]
[1443, 1444, Quantity(value=0.09572, unit=nanometer)]
[1443, 1445, Quantity(value=0.09572, unit=nanometer)]
[1446, 1447, Quantity(value=0.09572, unit=nanometer)]
[1446, 1448, Quantity(value=0.09572, unit=nanometer)]
[1449, 1450, Quantity(value=0.09572, unit=nanometer)]
[1449, 1451, Quantity(value=0.09572, unit=nanometer)]
[1452, 1453, Quantity(value=0.09572, unit=nanometer)]
[1452, 1454, Quantity(value=0.09572, unit=nanometer)]
[1455, 1456, Quantity(value=0.09572, unit=nanometer)]
[1455, 1457, Quantity(value=0.09572, unit=nanometer)]
[1458, 1459, Quantity(value=0.09572, unit=nanometer)]
[1458, 1460, Quantity(value=0.09572, unit=nanometer)]
[1461, 1462, Quantity(value=0.09572, unit=nanometer)]
[1461, 1463, Quantity(value=0.09572, unit=nanometer)]
[1464, 1465, Quantity(value=

[5073, 5074, Quantity(value=0.09572, unit=nanometer)]
[5073, 5075, Quantity(value=0.09572, unit=nanometer)]
[5076, 5077, Quantity(value=0.09572, unit=nanometer)]
[5076, 5078, Quantity(value=0.09572, unit=nanometer)]
[5079, 5080, Quantity(value=0.09572, unit=nanometer)]
[5079, 5081, Quantity(value=0.09572, unit=nanometer)]
[5082, 5083, Quantity(value=0.09572, unit=nanometer)]
[5082, 5084, Quantity(value=0.09572, unit=nanometer)]
[5085, 5086, Quantity(value=0.09572, unit=nanometer)]
[5085, 5087, Quantity(value=0.09572, unit=nanometer)]
[5088, 5089, Quantity(value=0.09572, unit=nanometer)]
[5088, 5090, Quantity(value=0.09572, unit=nanometer)]
[5091, 5092, Quantity(value=0.09572, unit=nanometer)]
[5091, 5093, Quantity(value=0.09572, unit=nanometer)]
[5094, 5095, Quantity(value=0.09572, unit=nanometer)]
[5094, 5096, Quantity(value=0.09572, unit=nanometer)]
[5097, 5098, Quantity(value=0.09572, unit=nanometer)]
[5097, 5099, Quantity(value=0.09572, unit=nanometer)]
[5100, 5101, Quantity(value=

[8820, 8822, Quantity(value=0.09572, unit=nanometer)]
[8823, 8824, Quantity(value=0.09572, unit=nanometer)]
[8823, 8825, Quantity(value=0.09572, unit=nanometer)]
[8826, 8827, Quantity(value=0.09572, unit=nanometer)]
[8826, 8828, Quantity(value=0.09572, unit=nanometer)]
[8829, 8830, Quantity(value=0.09572, unit=nanometer)]
[8829, 8831, Quantity(value=0.09572, unit=nanometer)]
[8832, 8833, Quantity(value=0.09572, unit=nanometer)]
[8832, 8834, Quantity(value=0.09572, unit=nanometer)]
[8835, 8836, Quantity(value=0.09572, unit=nanometer)]
[8835, 8837, Quantity(value=0.09572, unit=nanometer)]
[8838, 8839, Quantity(value=0.09572, unit=nanometer)]
[8838, 8840, Quantity(value=0.09572, unit=nanometer)]
[8841, 8842, Quantity(value=0.09572, unit=nanometer)]
[8841, 8843, Quantity(value=0.09572, unit=nanometer)]
[8844, 8845, Quantity(value=0.09572, unit=nanometer)]
[8844, 8846, Quantity(value=0.09572, unit=nanometer)]
[8847, 8848, Quantity(value=0.09572, unit=nanometer)]
[8847, 8849, Quantity(value=

[12570, 12572, Quantity(value=0.09572, unit=nanometer)]
[12573, 12574, Quantity(value=0.09572, unit=nanometer)]
[12573, 12575, Quantity(value=0.09572, unit=nanometer)]
[12576, 12577, Quantity(value=0.09572, unit=nanometer)]
[12576, 12578, Quantity(value=0.09572, unit=nanometer)]
[12579, 12580, Quantity(value=0.09572, unit=nanometer)]
[12579, 12581, Quantity(value=0.09572, unit=nanometer)]
[12582, 12583, Quantity(value=0.09572, unit=nanometer)]
[12582, 12584, Quantity(value=0.09572, unit=nanometer)]
[12585, 12586, Quantity(value=0.09572, unit=nanometer)]
[12585, 12587, Quantity(value=0.09572, unit=nanometer)]
[12588, 12589, Quantity(value=0.09572, unit=nanometer)]
[12588, 12590, Quantity(value=0.09572, unit=nanometer)]
[12591, 12592, Quantity(value=0.09572, unit=nanometer)]
[12591, 12593, Quantity(value=0.09572, unit=nanometer)]
[12594, 12595, Quantity(value=0.09572, unit=nanometer)]
[12594, 12596, Quantity(value=0.09572, unit=nanometer)]
[12597, 12598, Quantity(value=0.09572, unit=nano

[4360, 4361, Quantity(value=0.15139006545247014, unit=nanometer)]
[4363, 4364, Quantity(value=0.15139006545247014, unit=nanometer)]
[4366, 4367, Quantity(value=0.15139006545247014, unit=nanometer)]
[4369, 4370, Quantity(value=0.15139006545247014, unit=nanometer)]
[4372, 4373, Quantity(value=0.15139006545247014, unit=nanometer)]
[4375, 4376, Quantity(value=0.15139006545247014, unit=nanometer)]
[4378, 4379, Quantity(value=0.15139006545247014, unit=nanometer)]
[4381, 4382, Quantity(value=0.15139006545247014, unit=nanometer)]
[4384, 4385, Quantity(value=0.15139006545247014, unit=nanometer)]
[4387, 4388, Quantity(value=0.15139006545247014, unit=nanometer)]
[4390, 4391, Quantity(value=0.15139006545247014, unit=nanometer)]
[4393, 4394, Quantity(value=0.15139006545247014, unit=nanometer)]
[4396, 4397, Quantity(value=0.15139006545247014, unit=nanometer)]
[4399, 4400, Quantity(value=0.15139006545247014, unit=nanometer)]
[4402, 4403, Quantity(value=0.15139006545247014, unit=nanometer)]
[4405, 440

[11860, 11861, Quantity(value=0.15139006545247014, unit=nanometer)]
[11863, 11864, Quantity(value=0.15139006545247014, unit=nanometer)]
[11866, 11867, Quantity(value=0.15139006545247014, unit=nanometer)]
[11869, 11870, Quantity(value=0.15139006545247014, unit=nanometer)]
[11872, 11873, Quantity(value=0.15139006545247014, unit=nanometer)]
[11875, 11876, Quantity(value=0.15139006545247014, unit=nanometer)]
[11878, 11879, Quantity(value=0.15139006545247014, unit=nanometer)]
[11881, 11882, Quantity(value=0.15139006545247014, unit=nanometer)]
[11884, 11885, Quantity(value=0.15139006545247014, unit=nanometer)]
[11887, 11888, Quantity(value=0.15139006545247014, unit=nanometer)]
[11890, 11891, Quantity(value=0.15139006545247014, unit=nanometer)]
[11893, 11894, Quantity(value=0.15139006545247014, unit=nanometer)]
[11896, 11897, Quantity(value=0.15139006545247014, unit=nanometer)]
[11899, 11900, Quantity(value=0.15139006545247014, unit=nanometer)]
[11902, 11903, Quantity(value=0.1513900654524701

In [20]:
## --> Apo_htf has HBond constraints
## --> now, it doesn't anymore

In [ ]:
# Set up logger
import logging
_logger = logging.getLogger()
_logger.setLevel(logging.INFO)

In [11]:
# Solvent
from perses.app.relative_point_mutation_setup import PointMutationExecutor
from simtk import unit
solvent_delivery = PointMutationExecutor("../input/mmc2_barstar_T42A.pdb", 
                        '1', # First chain is the barstar one
                        '42', 
                        'THR',
                        ligand_file="../input/mmc2_barnase.pdb",
                        ionic_strength=0.05*unit.molar,
                        forcefield_kwargs={'removeCMMotion': False, 'ewaldErrorTolerance': 0.00025, 'hydrogenMass' : 4 * unit.amus}
                       )




RDKit WARNING: [13:37:42] Enabling RDKit 2019.09.3 jupyter extensions
INFO:root:solvating at 0.05 M using tip3p
INFO:root:solvating at 0.05 M using tip3p
INFO:proposal_generator:	Conducting polymer point mutation proposal...
INFO:proposal_generator:Using matching_criterion to chose best atom map
INFO:proposal_generator:Scaffold has symmetry of 0
INFO:proposal_generator:len [{4: 4, 9: 9}]
INFO:proposal_generator:{4: 4, 9: 9}
INFO:proposal_generator:Only one map so returning that one
INFO:proposal_generator:{4: 4, 9: 9}
INFO:geometry:propose: performing forward proposal
INFO:geometry:propose: unique new atoms detected; proceeding to _logp_propose...
INFO:geometry:Conducting forward proposal...
INFO:geometry:Computing proposal order with NetworkX...
INFO:geometry:number of atoms to be placed: 7
INFO:geometry:Atom index proposal order is [677, 681, 682, 678, 676, 679, 680]
INFO:geometry:omitted_bonds: []
INFO:geometry:direction of proposal is forward; creating atoms_with_positions and new 

conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA


INFO:geometry:setting atoms_with_positions context new positions


conducting subsequent work with the following platform: CUDA


INFO:geometry:There are 7 new atoms
INFO:geometry:	reduced angle potential = 0.39412877755325443.
INFO:geometry:	reduced angle potential = 0.15339123097012855.
INFO:geometry:	reduced angle potential = 0.540629955134827.
INFO:geometry:	reduced angle potential = 0.014846207702775366.
INFO:geometry:	reduced angle potential = 0.2982237687173077.
INFO:geometry:	reduced angle potential = 0.08122051947477.
INFO:geometry:	reduced angle potential = 0.1369764632679804.
INFO:geometry:	beginning construction of no_nonbonded final system...
INFO:geometry:	initial no-nonbonded final system forces ['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce', 'MonteCarloBarostat']
INFO:geometry:	final no-nonbonded final system forces dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce'])
INFO:geometry:	there are 1454 bond forces in the no-nonbonded final system
INFO:geometry:	there are 2635 angle forces in the no-nonbonded final system


...

conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA


INFO:geometry:total reduced energy added from growth system: 13.577305614641952
INFO:geometry:final reduced energy 4822.1069313279595
INFO:geometry:sum of energies: 4822.106931109809
INFO:geometry:magnitude of difference in the energies: 2.1815031026051201e-07
INFO:geometry:Final logp_proposal: 22.435618115610303


added energy components: [('CustomBondForce', 0.0008469410439007569), ('CustomAngleForce', 4.846819063425078), ('CustomTorsionForce', 0.12104886474337986), ('CustomBondForce', 8.608590745429597)]


INFO:relative:Beginning nonbonded method, total particle, barostat, and exceptions retrieval...
INFO:relative:Old system forces: dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce', 'MonteCarloBarostat'])
INFO:relative:New system forces: dict_keys(['HarmonicBondForce', 'HarmonicAngleForce', 'PeriodicTorsionForce', 'NonbondedForce', 'MonteCarloBarostat'])
INFO:relative:No unknown forces.
INFO:relative:Nonbonded method to be used (i.e. from old system): 4
INFO:relative:Adding and mapping old atoms to hybrid system...
INFO:relative:Adding and mapping new atoms to hybrid system...
INFO:relative:Added MonteCarloBarostat.
INFO:relative:getDefaultPeriodicBoxVectors added to hybrid: [Quantity(value=Vec3(x=6.7997, y=0.0, z=0.0), unit=nanometer), Quantity(value=Vec3(x=0.0, y=6.7997, z=0.0), unit=nanometer), Quantity(value=Vec3(x=0.0, y=0.0, z=6.7997), unit=nanometer)]
INFO:relative:Determined atom classes.
INFO:relative:Generating old system exceptions 

conducting subsequent work with the following platform: CUDA
conducting subsequent work with the following platform: CUDA
			HarmonicBondForce: 197.0361719691133
			HarmonicAngleForce: 795.3080247863992
			PeriodicTorsionForce: 3821.154143310387
			NonbondedForce: -25382.10826691071
			AndersenThermostat: 0.0
			MonteCarloBarostat: 0.0
conducting subsequent work with the following platform: CUDA
			CustomBondForce: 2.186963100265723
			HarmonicBondForce: 198.43264595267476
			CustomAngleForce: 7.0041135603192055
			HarmonicAngleForce: 789.8175509959092
			CustomTorsionForce: 0.050079561361173065
			PeriodicTorsionForce: 3836.8494050433815
			NonbondedForce: -25393.694078228047
			CustomNonbondedForce: -68.35558268547156
			CustomBondForce: 0.0
			AndersenThermostat: 0.0
			MonteCarloBarostat: 0.0
conducting subsequent work with the following platform: CUDA
			CustomBondForce: 2.186963100265723
			HarmonicBondForce: 198.43264595267476
			CustomAngleForce: 7.0041135603192055
			HarmonicA

In [16]:
import pickle
import os
out_dir = '/data/chodera/zhangi/perses_benchmark/neq/8/'
pickle.dump(solvent_delivery.get_apo_htf(), open(os.path.join(out_dir, "3/3_apo.pickle"), "wb" ))


In [13]:
import mdtraj as md
import numpy as np
htfs_t = [solvent_delivery.get_apo_htf(), solvent_delivery.get_complex_htf()]

top_old = md.Topology.from_openmm(htfs_t[0]._topology_proposal.old_topology)
top_new = md.Topology.from_openmm(htfs_t[0]._topology_proposal.new_topology)
traj = md.Trajectory(np.array(htfs_t[0].old_positions(htfs_t[0].hybrid_positions)), top_old)
traj.save("3_apo_old.pdb")
traj = md.Trajectory(np.array(htfs_t[0].new_positions(htfs_t[0].hybrid_positions)), top_new)
traj.save("3_apo_new.pdb")
